In [1]:
import pandas as pd
import numpy as np
from scipy.sparse import hstack
from wordcloud import WordCloud, STOPWORDS
import unicodedata
import re
from nltk.stem import PorterStemmer, WordNetLemmatizer, SnowballStemmer
from nltk.tokenize import TreebankWordTokenizer, sent_tokenize, word_tokenize, TweetTokenizer
from nltk.corpus import stopwords
from nltk.draw.dispersion import dispersion_plot
from sklearn.model_selection import cross_val_score
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
from sklearn.linear_model import LogisticRegression  
import emoji 
import sys
import string
from os import cpu_count
stop_words = set(stopwords.words('english'))
from matplotlib import pyplot as plt
from matplotlib import gridspec
import seaborn as sns
sns.set_style("dark")
%matplotlib inline

In [17]:
#  from gensim.parsing.preprocessing import 

In [29]:
# http://www.unicode.org/emoji/charts/full-emoji-list.html
# https://www.webfx.com/tools/emoji-cheat-sheet/

In [2]:
train = pd.read_csv('train.csv')
test = pd.read_csv('test.csv')

In [228]:
def cleaning_data(noizy_comment):
    noizy_comment= re.sub(r'http\S+', '', noizy_comment)
    noizy_comment = noizy_comment.lower()
    noizy_comment = re.sub(r"what's", "what is ", noizy_comment)
    noizy_comment = re.sub(r"\'s", " ", noizy_comment)
    noizy_comment = re.sub(r"\'ve", " have ", noizy_comment)
    noizy_comment = re.sub(r"can't", "cannot ", noizy_comment)
    noizy_comment = re.sub(r"n't", " not ", noizy_comment)
    noizy_comment = re.sub(r"i'm", "i am ", noizy_comment)
    noizy_comment = re.sub(r"\'re", " are ", noizy_comment)
    noizy_comment = re.sub(r"\'d", " would ", noizy_comment)
    noizy_comment = re.sub(r"\'ll", " will ", noizy_comment)
    noizy_comment = re.sub(r"\'scuse", " excuse ", noizy_comment)
    noizy_comment = re.sub(r'\W', ' ', noizy_comment)
    noizy_comment = re.sub(r'\s+', ' ', noizy_comment)
    noizy_comment = re.sub(' +',' ',noizy_comment)
    noizy_comment = re.sub(r'\n',' ',noizy_comment)
    noizy_comment = noizy_comment.strip(' ')
    cleaned_comment = noizy_comment
    return cleaned_comment

In [3]:
alltext = train.comment_text.str.cat(sep=' ')

In [31]:
# chr(65)

'A'

In [80]:
# unicodedata.category(chr(65))

'Lu'

In [4]:
len(alltext)

63042228

In [5]:
%%time
UNICODE_EMOJI = {
    k: f" EMJ {v.strip(':').replace('_', ' ')} "
    for k, v in emoji.UNICODE_EMOJI_ALIAS.items()
}
def extract_emojis(text):
    return ''.join(UNICODE_EMOJI[c] if c in UNICODE_EMOJI else c for c in text )
alltext = extract_emojis(alltext)

Wall time: 11.4 s


In [6]:
len(alltext)

63065382

In [7]:
CUSTOM_TABLE = str.maketrans(
    {
        "\xad": None,
        "\x7f": None,
        "\ufeff": None,
        "\u200b": None,
        "\u200e": None,
        "\u202a": None,
        "\u202c": None,
        "‘": "'",
        "’": "'",
        "`": "'",
        "´": "'",
        "“": '"',
        "”": '"',
        "«": '"',
        "»": '"',
        "ɢ": "G",
        "ɪ": "I",
        "ɴ": "N",
        "ʀ": "R",
        "ʏ": "Y",
        "ʙ": "B",
        "ʜ": "H",
        "ʟ": "L",
        "ғ": "F",
        "ᴀ": "A",
        "ᴄ": "C",
        "ᴅ": "D",
        "ᴇ": "E",
        "ᴊ": "J",
        "ᴋ": "K",
        "ᴍ": "M",
        "Μ": "M",
        "ᴏ": "O",
        "ᴘ": "P",
        "ᴛ": "T",
        "ᴜ": "U",
        "ᴡ": "W",
        "ᴠ": "V",
        "ĸ": "K",
        "в": "B",
        "м": "M",
        "н": "H",
        "т": "T",
        "ѕ": "S",
        "—": "-",
        "–": "-",
        "★": "*",
        "☆": "*",
        "¡": "!",
        "¿": "?",
        "（": "(",
        "）": ")",
        
    }
)

In [8]:
alltext = alltext.translate(CUSTOM_TABLE)

In [9]:
len(alltext)

63064592

In [10]:
WORDS_REPLACER = [
    ("sh*t", "shit"),
    ("s**t", "shit"),
    ("f*ck", "fuck"),
    ("fu*k", "fuck"),
    ("f**k", "fuck"),
    ("f*****g", "fucking"),
    ("f***ing", "fucking"),
    ("f**king", "fucking"),
    ("p*ssy", "pussy"),
    ("p***y", "pussy"),
    ("pu**y", "pussy"),
    ("p*ss", "piss"),
    ("b*tch", "bitch"),
    ("bit*h", "bitch"),
    ("h*ll", "hell"),
    ("h**l", "hell"),
    ("cr*p", "crap"),
    ("d*mn", "damn"),
    ("stu*pid", "stupid"),
    ("st*pid", "stupid"),
    ("n*gger", "nigger"),
    ("n***ga", "nigger"),
    ("f*ggot", "faggot"),
    ("scr*w", "screw"),
    ("pr*ck", "prick"),
    ("g*d", "god"),
    ("s*x", "sex"),
    ("a*s", "ass"),
    ("a**hole", "asshole"),
    ("a***ole", "asshole"),
    ("a**", "ass"),
]

In [11]:
%%time
REGEX_REPLACER = [
    (re.compile(pat.replace("*", "\*"), flags=re.IGNORECASE), repl)
    for pat, repl in WORDS_REPLACER
]

Wall time: 3 ms


In [12]:
'f*ck' in alltext

True

In [13]:
%%time
for pattern, repl in REGEX_REPLACER:
    alltext = pattern.sub(repl, alltext)


Wall time: 42 s


In [14]:
'f*ck' in alltext

False

In [15]:
'★' in alltext

False

In [16]:
len(alltext)

63064592

In [17]:
GODWORDS_REPLACER = {"'re": " are", "ain't": "is not", "aren't": "are not","can't": "cannot", "'cause": "because", 
                       "could've": "could have", "couldn't": "could not", "didn't": "did not",  "doesn't": "does not", 
                       "don't": "do not", "hadn't": "had not", "hasn't": "has not", "haven't": "have not", "he'd": "he would",
                       "he'll": "he will", "he's": "he is", "how'd": "how did", "how'd'y": "how do you", "how'll": "how will", 
                       "how's": "how is",  "I'd": "I would", "I'd've": "I would have", "I'll": "I will",
                       "I'll've": "I will have","I'm": "I am", "I've": "I have", "i'd": "i would", "i'd've": "i would have", 
                       "i'll": "i will",  "i'll've": "i will have","i'm": "i am", "i've": "i have", "isn't": "is not", 
                       "it'd": "it would", "it'd've": "it would have", "it'll": "it will", "it'll've": "it will have",
                       "it's": "it is", "let's": "let us", "ma'am": "madam", "mayn't": "may not", "might've": "might have",
                       "mightn't": "might not","mightn't've": "might not have", "must've": "must have", 
                       "mustn't": "must not", "mustn't've": "must not have", "needn't": "need not", 
                       "needn't've": "need not have","o'clock": "of the clock", "oughtn't": "ought not", 
                       "oughtn't've": "ought not have", "shan't": "shall not", "sha'n't": "shall not", 
                       "shan't've": "shall not have", "she'd": "she would", "she'd've": "she would have", 
                       "she'll": "she will", "she'll've": "she will have", "she's": "she is", "should've": "should have", 
                       "shouldn't": "should not", "shouldn't've": "should not have", "so've": "so have","so's": "so as", 
                       "this's": "this is","that'd": "that would", "that'd've": "that would have", "that's": "that is", 
                       "there'd": "there would", "there'd've": "there would have", "there's": "there is", 
                       "here's": "here is","they'd": "they would", "they'd've": "they would have", 
                       "they'll": "they will", "they'll've": "they will have", "they're": "they are", 
                       "they've": "they have", "to've": "to have", "wasn't": "was not", "we'd": "we would", 
                       "we'd've": "we would have", "we'll": "we will", "we'll've": "we will have", "we're": "we are", 
                       "we've": "we have", "weren't": "were not", "what'll": "what will", "what'll've": "what will have", 
                       "what're": "what are",  "what's": "what is", "what've": "what have", 
                       "when's": "when is", "when've": "when have", "where'd": "where did", "where's": "where is", 
                       "where've": "where have", "who'll": "who will", "who'll've": "who will have", 
                       "who's": "who is", "who've": "who have", "why's": "why is", "why've": "why have", 
                       "will've": "will have", "won't": "will not", "won't've": "will not have", "would've": "would have", 
                       "wouldn't": "would not", "wouldn't've": "would not have", "y'all": "you all", 
                       "y'all'd": "you all would","y'all'd've": "you all would have","y'all're": "you all are",
                       "y'all've": "you all have","you'd": "you would", "you'd've": "you would have", "you'll": "you will", 
                       "you'll've": "you will have", "you're": "you are", "you've": "you have" 
                                  }

In [18]:
%%time
# replacements = {'as': 'dfg', '1234': 'qw'}
alltext = re.sub('({})'.format('|'.join(map(re.escape, GODWORDS_REPLACER.keys()))), lambda m: GODWORDS_REPLACER[m.group()], alltext)

Wall time: 20.3 s


In [156]:
# TABLE.update(goodwords_replacer)


In [19]:
len(alltext)

63232436

In [20]:
alltext = alltext.lower()

In [21]:
len(alltext)

63232463

In [22]:
#to delete
OTHER_CONTROL_TABLE = dict.fromkeys(
    i for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "Cc"
)
len(OTHER_CONTROL_TABLE)

65

In [94]:
# #to delete
# OTHER_CONTROL_TABLE = {i : chr(i) for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "Cc"}

# len(OTHER_CONTROL_TABLE)

In [23]:
# TO DELETE
OTHER_FORMAT_TABLE = dict.fromkeys(
    i for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "Cf"
)
len(OTHER_FORMAT_TABLE)

151

In [24]:
# TO DELETE
NOT_ASSIGNED_TABLE = dict.fromkeys(
    i for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "Cn"
)
len(NOT_ASSIGNED_TABLE)

846359

In [25]:
# TO DELETE
PRIVATE_USE_TABLE = dict.fromkeys(
    i for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "Co"
)
len(PRIVATE_USE_TABLE)

# for key, value in PRIVATE_USE_TABLE.items():
#     PRIVATE_USE_TABLE[key] = chr(key)

137468

In [26]:
# TO DELETE
SURROGATE_TABLE = dict.fromkeys(
    i for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "Cs"
)
# for key, value in SURROGATE_TABLE.items():
#     SURROGATE_TABLE[key] = chr(key)

len(SURROGATE_TABLE)

2048

In [27]:
# TO DELETE
LETTERCASED_TABLE = dict.fromkeys(
    i for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "LC"
)
for key, value in LETTERCASED_TABLE.items():
    LETTERCASED_TABLE[key] = chr(key)

len(LETTERCASED_TABLE)

0

In [28]:
LETTERCASED_TABLE

{}

In [29]:
# DELETE but need fuuture work
LETTER_MODIFIER_TABLE = dict.fromkeys(
    i for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "Lm"
)
len(LETTER_MODIFIER_TABLE)

249

In [30]:
NONSPACING_TABLE = dict.fromkeys(
    i for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "Mn"
)

In [31]:
"★" in alltext

False

In [135]:
# alltext = alltext.translate(CUSTOM_TABLE)

In [32]:
"★" in alltext

False

In [33]:
TABLE = dict()
# TABLE.update(CUSTOM_TABLE)
TABLE.update(NONSPACING_TABLE)
TABLE.update(OTHER_CONTROL_TABLE)
TABLE.update(OTHER_FORMAT_TABLE)
TABLE.update(NOT_ASSIGNED_TABLE)
TABLE.update(PRIVATE_USE_TABLE)
# TABLE.update(LETTERCASED_TABLE)
TABLE.update(SURROGATE_TABLE)
# TABLE.update(SURROGATE_TABLE)
# TABLE.update(SURROGATE_TABLE)


# Non-english languages
# TABLE.update(CHINESE_TABLE)
# TABLE.update(HEBREW_TABLE)
# TABLE.update(ARABIC_TABLE)
# TABLE.update(HIRAGANA_TABLE)
# TABLE.update(KATAKANA_TABLE)
# TABLE.update(KANJI_TABLE)

In [34]:
len(alltext)

63232463

In [35]:
alltext = alltext.translate(TABLE)

In [36]:
63232463

63232463

In [37]:
len(alltext)

62829597

In [38]:
alltext[0:1000]

'explanationwhy the edits made under my username hardcore metallica fan were reverted? they were not vandalisms, just closure on some gas after i voted at new york dolls fac. and please do not remove the template from the talk page since i am retired now.89.205.38.27 d\'aww! he matches this background colour i am seemingly stuck with. thanks.  (talk) 21:51, january 11, 2016 (utc) hey man, i am really not trying to edit war. it\'s just that this guy is constantly removing relevant information and talking to me through edits instead of my talk page. he seems to care more about the formatting than the actual info. "morei cannot make any real suggestions on improvement - i wondered if the section statistics should be later on, or a subsection of ""types of accidents""  -i think the references may need tidying so that they are all in the exact same format ie date format etc. i can do that later on, if no-one else does first - if you have any preferences for formatting style on references or

In [39]:
#HappyEmoticons
emoticons_happy = set([
    ':-)', ':)', ';)', ':o)', ':]', ':3', ':c)', ':>', '=]', '8)', '=)', ':}',
    ':^)', ':-D', ':D', '8-D', '8D', 'x-D', 'xD', 'X-D', 'XD', '=-D', '=D',
    '=-3', '=3', ':-))', ":'-)", ":')", ':*', ':^*', '>:P', ':-P', ':P', 'X-P',
    'x-p', 'xp', 'XP', ':-p', ':p', '=p', ':-b', ':b', '>:)', '>;)', '>:-)',
    '<3'
    ])

In [40]:
alltext = TweetTokenizer().tokenize(alltext)

In [41]:
len(alltext)

12764242

In [42]:
12764242

12764242

In [43]:
# alltext = " ".join(i for i in alltext)

In [44]:
# Sad Emoticons
emoticons_sad = set([
    ':L', ':-/', '>:/', ':S', '>:[', ':@', ':-(', ':[', ':-||', '=L', ':<',
    ':-[', ':-<', '=\\', '=/', '>:(', ':(', '>.<', ":'-(", ":'(", ':\\', ':-c',
    ':c', ':{', '>:\\', ';('
    ])

In [45]:
alltext = ['emj sad' if i in emoticons_sad else i for i in alltext]
alltext = ['emj happy' if i in emoticons_happy else i for i in alltext]

In [46]:
alltext = " ".join(i for i in alltext)

In [47]:
len(alltext)

64563568

In [48]:
alltext = cleaning_data(alltext)

NameError: name 'cleaning_data' is not defined

In [51]:
alltext[0:10000]

'explanationwhy the edits made under my username hardcore metallica fan were reverted ? they were not vandalisms , just closure on some gas after i voted at new york dolls fac . and please do not remove the template from the talk page since i am retired now . 89.205 . 38.27 d\'aww ! he matches this background colour i am seemingly stuck with . thanks . ( talk ) 21:51 , january 11 , 2016 ( utc ) hey man , i am really not trying to edit war . it\'s just that this guy is constantly removing relevant information and talking to me through edits instead of my talk page . he seems to care more about the formatting than the actual info . " morei cannot make any real suggestions on improvement - i wondered if the section statistics should be later on , or a subsection of " " types of accidents " " - i think the references may need tidying so that they are all in the exact same format ie date format etc . i can do that later on , if no-one else does first - if you have any preferences for format

In [52]:
# alltext = mytext.translate(str.maketrans('', '', string.punctuation))

In [53]:
alltext = re.sub(r'^https?:\/\/.*[\r\n]*', '', alltext, flags=re.MULTILINE)

In [54]:
alltext = re.sub(r'http\S+', '', alltext)

In [55]:
len(alltext)

64129467

In [56]:
"sdasdsad 34343 df444ff".isalpha()

False

In [57]:
alltext[0:1000]

'explanationwhy the edits made under my username hardcore metallica fan were reverted ? they were not vandalisms , just closure on some gas after i voted at new york dolls fac . and please do not remove the template from the talk page since i am retired now . 89.205 . 38.27 d\'aww ! he matches this background colour i am seemingly stuck with . thanks . ( talk ) 21:51 , january 11 , 2016 ( utc ) hey man , i am really not trying to edit war . it\'s just that this guy is constantly removing relevant information and talking to me through edits instead of my talk page . he seems to care more about the formatting than the actual info . " morei cannot make any real suggestions on improvement - i wondered if the section statistics should be later on , or a subsection of " " types of accidents " " - i think the references may need tidying so that they are all in the exact same format ie date format etc . i can do that later on , if no-one else does first - if you have any preferences for format

In [58]:
len(result)

NameError: name 'result' is not defined

In [59]:
result = " ".join(result.split())

NameError: name 'result' is not defined

In [60]:
len(result)

NameError: name 'result' is not defined

In [63]:
%%time
phrase= alltext

patterns= [r'\W+']

    
for p in patterns:
    match= re.findall(p, phrase)
#     print(match)

Wall time: 4.37 s


In [64]:
len(match)

10954265

In [65]:
mytext = alltext

In [66]:
mytext = mytext.translate(str.maketrans('', '', string.punctuation))

In [67]:
len(mytext)

61866283

In [68]:
mytext[0:1000]

'explanationwhy the edits made under my username hardcore metallica fan were reverted  they were not vandalisms  just closure on some gas after i voted at new york dolls fac  and please do not remove the template from the talk page since i am retired now  89205  3827 daww  he matches this background colour i am seemingly stuck with  thanks   talk  2151  january 11  2016  utc  hey man  i am really not trying to edit war  its just that this guy is constantly removing relevant information and talking to me through edits instead of my talk page  he seems to care more about the formatting than the actual info   morei cannot make any real suggestions on improvement  i wondered if the section statistics should be later on  or a subsection of   types of accidents    i think the references may need tidying so that they are all in the exact same format ie date format etc  i can do that later on  if noone else does first  if you have any preferences for formatting style on references or want to d

In [69]:
mytext = " ".join(mytext.split())

In [70]:
mytext[0:1000]

'explanationwhy the edits made under my username hardcore metallica fan were reverted they were not vandalisms just closure on some gas after i voted at new york dolls fac and please do not remove the template from the talk page since i am retired now 89205 3827 daww he matches this background colour i am seemingly stuck with thanks talk 2151 january 11 2016 utc hey man i am really not trying to edit war its just that this guy is constantly removing relevant information and talking to me through edits instead of my talk page he seems to care more about the formatting than the actual info morei cannot make any real suggestions on improvement i wondered if the section statistics should be later on or a subsection of types of accidents i think the references may need tidying so that they are all in the exact same format ie date format etc i can do that later on if noone else does first if you have any preferences for formatting style on references or want to do it yourself please let me k

In [71]:
':L' in emoticons_sad

True

In [72]:
# MORE WORK
PUNCTUATION_OTHER_TABLE = dict.fromkeys(
    i for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "Po"
)
len(PUNCTUATION_OTHER_TABLE)

544

In [73]:
TABLE.update(PUNCTUATION_OTHER_TABLE)

In [74]:
mytext = mytext.translate(PUNCTUATION_OTHER_TABLE)

In [75]:
len(mytext)

59854189

In [76]:
mytext[0:1000]

'explanationwhy the edits made under my username hardcore metallica fan were reverted they were not vandalisms just closure on some gas after i voted at new york dolls fac and please do not remove the template from the talk page since i am retired now 89205 3827 daww he matches this background colour i am seemingly stuck with thanks talk 2151 january 11 2016 utc hey man i am really not trying to edit war its just that this guy is constantly removing relevant information and talking to me through edits instead of my talk page he seems to care more about the formatting than the actual info morei cannot make any real suggestions on improvement i wondered if the section statistics should be later on or a subsection of types of accidents i think the references may need tidying so that they are all in the exact same format ie date format etc i can do that later on if noone else does first if you have any preferences for formatting style on references or want to do it yourself please let me k

In [77]:
unicodedata.category('െ')

'Mc'

In [78]:
# MORE WORK
SPACING_COMBINING_TABLE = dict.fromkeys(
    i for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "Mc"
)
len(SPACING_COMBINING_TABLE)

394

In [79]:
TABLE.update(SPACING_COMBINING_TABLE)

In [80]:
mytext = mytext.translate(TABLE)

In [81]:
len(mytext)

59853938

In [82]:
mytext[0:1000]

'explanationwhy the edits made under my username hardcore metallica fan were reverted they were not vandalisms just closure on some gas after i voted at new york dolls fac and please do not remove the template from the talk page since i am retired now 89205 3827 daww he matches this background colour i am seemingly stuck with thanks talk 2151 january 11 2016 utc hey man i am really not trying to edit war its just that this guy is constantly removing relevant information and talking to me through edits instead of my talk page he seems to care more about the formatting than the actual info morei cannot make any real suggestions on improvement i wondered if the section statistics should be later on or a subsection of types of accidents i think the references may need tidying so that they are all in the exact same format ie date format etc i can do that later on if noone else does first if you have any preferences for formatting style on references or want to do it yourself please let me k

In [83]:
unicodedata.category('¤')

'Sc'

In [84]:
CURRENCY_TABLE = dict.fromkeys(
    i for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "Sc"
)
len(CURRENCY_TABLE)

53

In [85]:
TABLE.update(CURRENCY_TABLE)

In [86]:
mytext = mytext.translate(TABLE)

In [87]:
len(mytext)

59853539

In [88]:
mytext[0:1000]

'explanationwhy the edits made under my username hardcore metallica fan were reverted they were not vandalisms just closure on some gas after i voted at new york dolls fac and please do not remove the template from the talk page since i am retired now 89205 3827 daww he matches this background colour i am seemingly stuck with thanks talk 2151 january 11 2016 utc hey man i am really not trying to edit war its just that this guy is constantly removing relevant information and talking to me through edits instead of my talk page he seems to care more about the formatting than the actual info morei cannot make any real suggestions on improvement i wondered if the section statistics should be later on or a subsection of types of accidents i think the references may need tidying so that they are all in the exact same format ie date format etc i can do that later on if noone else does first if you have any preferences for formatting style on references or want to do it yourself please let me k

In [89]:
mytext = " ".join(mytext.split())

In [90]:
len(mytext)

59844516

In [91]:
mytext[0:1000]

'explanationwhy the edits made under my username hardcore metallica fan were reverted they were not vandalisms just closure on some gas after i voted at new york dolls fac and please do not remove the template from the talk page since i am retired now 89205 3827 daww he matches this background colour i am seemingly stuck with thanks talk 2151 january 11 2016 utc hey man i am really not trying to edit war its just that this guy is constantly removing relevant information and talking to me through edits instead of my talk page he seems to care more about the formatting than the actual info morei cannot make any real suggestions on improvement i wondered if the section statistics should be later on or a subsection of types of accidents i think the references may need tidying so that they are all in the exact same format ie date format etc i can do that later on if noone else does first if you have any preferences for formatting style on references or want to do it yourself please let me k

In [92]:
unicodedata.category('」')

'Pe'

In [93]:
PUNCTUATION_CLOSE_TABLE = dict.fromkeys(
    i for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "Pe"
)
len(PUNCTUATION_CLOSE_TABLE)

73

In [94]:
TABLE.update(PUNCTUATION_CLOSE_TABLE)

In [95]:
mytext = mytext.translate(TABLE)

In [96]:
len(mytext)

59844485

In [97]:
mytext[0:1000]

'explanationwhy the edits made under my username hardcore metallica fan were reverted they were not vandalisms just closure on some gas after i voted at new york dolls fac and please do not remove the template from the talk page since i am retired now 89205 3827 daww he matches this background colour i am seemingly stuck with thanks talk 2151 january 11 2016 utc hey man i am really not trying to edit war its just that this guy is constantly removing relevant information and talking to me through edits instead of my talk page he seems to care more about the formatting than the actual info morei cannot make any real suggestions on improvement i wondered if the section statistics should be later on or a subsection of types of accidents i think the references may need tidying so that they are all in the exact same format ie date format etc i can do that later on if noone else does first if you have any preferences for formatting style on references or want to do it yourself please let me k

In [98]:
mytext = " ".join(mytext.split())

In [99]:
len(mytext)

59844454

In [100]:
unicodedata.category('「')

'Ps'

In [101]:
PUNCTUATION_OPEN_TABLE = dict.fromkeys(
    i for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "Ps"
)
len(PUNCTUATION_OPEN_TABLE)

75

In [102]:
TABLE.update(PUNCTUATION_OPEN_TABLE)

In [103]:
mytext = mytext.translate(TABLE)

In [104]:
len(mytext)

59844386

In [105]:
mytext[0:1000]

'explanationwhy the edits made under my username hardcore metallica fan were reverted they were not vandalisms just closure on some gas after i voted at new york dolls fac and please do not remove the template from the talk page since i am retired now 89205 3827 daww he matches this background colour i am seemingly stuck with thanks talk 2151 january 11 2016 utc hey man i am really not trying to edit war its just that this guy is constantly removing relevant information and talking to me through edits instead of my talk page he seems to care more about the formatting than the actual info morei cannot make any real suggestions on improvement i wondered if the section statistics should be later on or a subsection of types of accidents i think the references may need tidying so that they are all in the exact same format ie date format etc i can do that later on if noone else does first if you have any preferences for formatting style on references or want to do it yourself please let me k

In [106]:
mytext = " ".join(mytext.split())

In [107]:
len(mytext)

59844318

In [108]:
unicodedata.category('↑')

'Sm'

In [109]:
SYMBOL_MATH_TABLE = dict.fromkeys(
    i for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "Sm"
)
len(SYMBOL_MATH_TABLE)

948

In [110]:
TABLE.update(SYMBOL_MATH_TABLE)

In [111]:
mytext = mytext.translate(TABLE)

In [112]:
len(mytext)

59842667

In [113]:
TweetTokenizer().tokenize('◕‿◕')

['◕', '‿', '◕']

In [114]:
mytext[0:1000]

'explanationwhy the edits made under my username hardcore metallica fan were reverted they were not vandalisms just closure on some gas after i voted at new york dolls fac and please do not remove the template from the talk page since i am retired now 89205 3827 daww he matches this background colour i am seemingly stuck with thanks talk 2151 january 11 2016 utc hey man i am really not trying to edit war its just that this guy is constantly removing relevant information and talking to me through edits instead of my talk page he seems to care more about the formatting than the actual info morei cannot make any real suggestions on improvement i wondered if the section statistics should be later on or a subsection of types of accidents i think the references may need tidying so that they are all in the exact same format ie date format etc i can do that later on if noone else does first if you have any preferences for formatting style on references or want to do it yourself please let me k

In [115]:
mytext = " ".join(mytext.split())

In [116]:
len(mytext)

59841016

In [117]:
unicodedata.category('№')

'So'

In [118]:
#WORK
SYMBOL_OTHER_TABLE = dict.fromkeys(
    i for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "So"
)
len(SYMBOL_OTHER_TABLE)

5777

In [119]:
TABLE.update(SYMBOL_OTHER_TABLE)

In [120]:
mytext = mytext.translate(TABLE)

In [121]:
len(mytext)

59839524

In [122]:
mytext[0:1000]

'explanationwhy the edits made under my username hardcore metallica fan were reverted they were not vandalisms just closure on some gas after i voted at new york dolls fac and please do not remove the template from the talk page since i am retired now 89205 3827 daww he matches this background colour i am seemingly stuck with thanks talk 2151 january 11 2016 utc hey man i am really not trying to edit war its just that this guy is constantly removing relevant information and talking to me through edits instead of my talk page he seems to care more about the formatting than the actual info morei cannot make any real suggestions on improvement i wondered if the section statistics should be later on or a subsection of types of accidents i think the references may need tidying so that they are all in the exact same format ie date format etc i can do that later on if noone else does first if you have any preferences for formatting style on references or want to do it yourself please let me k

In [123]:
mytext = " ".join(mytext.split())

In [124]:
len(mytext)

59838032

In [125]:
unicodedata.category('´')

'Sk'

In [126]:
#WORK
SYMBOL_MODIFIER_TABLE = dict.fromkeys(
    i for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "Sk"
)
len(SYMBOL_MODIFIER_TABLE)

121

In [127]:
TABLE.update(SYMBOL_MODIFIER_TABLE)

In [128]:
mytext = mytext.translate(TABLE)

In [129]:
len(mytext)

59837912

In [130]:
mytext[0:1000]

'explanationwhy the edits made under my username hardcore metallica fan were reverted they were not vandalisms just closure on some gas after i voted at new york dolls fac and please do not remove the template from the talk page since i am retired now 89205 3827 daww he matches this background colour i am seemingly stuck with thanks talk 2151 january 11 2016 utc hey man i am really not trying to edit war its just that this guy is constantly removing relevant information and talking to me through edits instead of my talk page he seems to care more about the formatting than the actual info morei cannot make any real suggestions on improvement i wondered if the section statistics should be later on or a subsection of types of accidents i think the references may need tidying so that they are all in the exact same format ie date format etc i can do that later on if noone else does first if you have any preferences for formatting style on references or want to do it yourself please let me k

In [131]:
mytext = " ".join(mytext.split())

In [132]:
len(mytext)

59837792

In [133]:
mytext[0:1000]

'explanationwhy the edits made under my username hardcore metallica fan were reverted they were not vandalisms just closure on some gas after i voted at new york dolls fac and please do not remove the template from the talk page since i am retired now 89205 3827 daww he matches this background colour i am seemingly stuck with thanks talk 2151 january 11 2016 utc hey man i am really not trying to edit war its just that this guy is constantly removing relevant information and talking to me through edits instead of my talk page he seems to care more about the formatting than the actual info morei cannot make any real suggestions on improvement i wondered if the section statistics should be later on or a subsection of types of accidents i think the references may need tidying so that they are all in the exact same format ie date format etc i can do that later on if noone else does first if you have any preferences for formatting style on references or want to do it yourself please let me k

In [134]:
unicodedata.category('―')

'Pd'

In [135]:
#WORK
PUNCTUATION_DASH_TABLE = dict.fromkeys(
    i for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "Pd"
)
len(PUNCTUATION_DASH_TABLE)

24

In [136]:
TABLE.update(PUNCTUATION_DASH_TABLE)

In [137]:
mytext = mytext.translate(TABLE)

In [138]:
len(mytext)

59837752

In [139]:
mytext[0:1000]

'explanationwhy the edits made under my username hardcore metallica fan were reverted they were not vandalisms just closure on some gas after i voted at new york dolls fac and please do not remove the template from the talk page since i am retired now 89205 3827 daww he matches this background colour i am seemingly stuck with thanks talk 2151 january 11 2016 utc hey man i am really not trying to edit war its just that this guy is constantly removing relevant information and talking to me through edits instead of my talk page he seems to care more about the formatting than the actual info morei cannot make any real suggestions on improvement i wondered if the section statistics should be later on or a subsection of types of accidents i think the references may need tidying so that they are all in the exact same format ie date format etc i can do that later on if noone else does first if you have any preferences for formatting style on references or want to do it yourself please let me k

In [140]:
mytext = " ".join(mytext.split())

In [141]:
len(mytext)

59837712

In [142]:
mytext[0:1000]

'explanationwhy the edits made under my username hardcore metallica fan were reverted they were not vandalisms just closure on some gas after i voted at new york dolls fac and please do not remove the template from the talk page since i am retired now 89205 3827 daww he matches this background colour i am seemingly stuck with thanks talk 2151 january 11 2016 utc hey man i am really not trying to edit war its just that this guy is constantly removing relevant information and talking to me through edits instead of my talk page he seems to care more about the formatting than the actual info morei cannot make any real suggestions on improvement i wondered if the section statistics should be later on or a subsection of types of accidents i think the references may need tidying so that they are all in the exact same format ie date format etc i can do that later on if noone else does first if you have any preferences for formatting style on references or want to do it yourself please let me k

In [143]:
unicodedata.category('‿')

'Pc'

In [144]:
#WORK
PUNCTUATION_CONNECTOR_TABLE = dict.fromkeys(
    i for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "Pc"
)
len(PUNCTUATION_CONNECTOR_TABLE)

10

In [145]:
TABLE.update(PUNCTUATION_CONNECTOR_TABLE)

In [146]:
mytext = mytext.translate(TABLE)

In [147]:
len(mytext)

59837693

In [148]:
mytext[0:1000]

'explanationwhy the edits made under my username hardcore metallica fan were reverted they were not vandalisms just closure on some gas after i voted at new york dolls fac and please do not remove the template from the talk page since i am retired now 89205 3827 daww he matches this background colour i am seemingly stuck with thanks talk 2151 january 11 2016 utc hey man i am really not trying to edit war its just that this guy is constantly removing relevant information and talking to me through edits instead of my talk page he seems to care more about the formatting than the actual info morei cannot make any real suggestions on improvement i wondered if the section statistics should be later on or a subsection of types of accidents i think the references may need tidying so that they are all in the exact same format ie date format etc i can do that later on if noone else does first if you have any preferences for formatting style on references or want to do it yourself please let me k

In [149]:
mytext = " ".join(mytext.split())

In [150]:
len(mytext)

59837674

In [151]:
mytext[0:1000]

'explanationwhy the edits made under my username hardcore metallica fan were reverted they were not vandalisms just closure on some gas after i voted at new york dolls fac and please do not remove the template from the talk page since i am retired now 89205 3827 daww he matches this background colour i am seemingly stuck with thanks talk 2151 january 11 2016 utc hey man i am really not trying to edit war its just that this guy is constantly removing relevant information and talking to me through edits instead of my talk page he seems to care more about the formatting than the actual info morei cannot make any real suggestions on improvement i wondered if the section statistics should be later on or a subsection of types of accidents i think the references may need tidying so that they are all in the exact same format ie date format etc i can do that later on if noone else does first if you have any preferences for formatting style on references or want to do it yourself please let me k

In [152]:
unicodedata.category('›')

'Pf'

In [153]:
#WORK
PUNCTUATION_FINAL_QUOTE_TABLE = dict.fromkeys(
    i for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "Pf"
)
len(PUNCTUATION_FINAL_QUOTE_TABLE)

10

In [154]:
TABLE.update(PUNCTUATION_FINAL_QUOTE_TABLE)

In [155]:
mytext = mytext.translate(TABLE)

In [156]:
len(mytext)

59837667

In [157]:
mytext[0:1000]

'explanationwhy the edits made under my username hardcore metallica fan were reverted they were not vandalisms just closure on some gas after i voted at new york dolls fac and please do not remove the template from the talk page since i am retired now 89205 3827 daww he matches this background colour i am seemingly stuck with thanks talk 2151 january 11 2016 utc hey man i am really not trying to edit war its just that this guy is constantly removing relevant information and talking to me through edits instead of my talk page he seems to care more about the formatting than the actual info morei cannot make any real suggestions on improvement i wondered if the section statistics should be later on or a subsection of types of accidents i think the references may need tidying so that they are all in the exact same format ie date format etc i can do that later on if noone else does first if you have any preferences for formatting style on references or want to do it yourself please let me k

In [158]:
mytext = " ".join(mytext.split())

In [159]:
len(mytext)

59837660

In [160]:
mytext[0:1000]

'explanationwhy the edits made under my username hardcore metallica fan were reverted they were not vandalisms just closure on some gas after i voted at new york dolls fac and please do not remove the template from the talk page since i am retired now 89205 3827 daww he matches this background colour i am seemingly stuck with thanks talk 2151 january 11 2016 utc hey man i am really not trying to edit war its just that this guy is constantly removing relevant information and talking to me through edits instead of my talk page he seems to care more about the formatting than the actual info morei cannot make any real suggestions on improvement i wondered if the section statistics should be later on or a subsection of types of accidents i think the references may need tidying so that they are all in the exact same format ie date format etc i can do that later on if noone else does first if you have any preferences for formatting style on references or want to do it yourself please let me k

In [161]:
unicodedata.category('‹')

'Pi'

In [162]:
#WORK
PUNCTUATION_INITIAL_QUOTE_TABLE = dict.fromkeys(
    i for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "Pi"
)
len(PUNCTUATION_INITIAL_QUOTE_TABLE)

12

In [163]:
TABLE.update(PUNCTUATION_INITIAL_QUOTE_TABLE)

In [164]:
mytext = mytext.translate(TABLE)

In [165]:
len(mytext)

59837653

In [166]:
mytext[0:1000]

'explanationwhy the edits made under my username hardcore metallica fan were reverted they were not vandalisms just closure on some gas after i voted at new york dolls fac and please do not remove the template from the talk page since i am retired now 89205 3827 daww he matches this background colour i am seemingly stuck with thanks talk 2151 january 11 2016 utc hey man i am really not trying to edit war its just that this guy is constantly removing relevant information and talking to me through edits instead of my talk page he seems to care more about the formatting than the actual info morei cannot make any real suggestions on improvement i wondered if the section statistics should be later on or a subsection of types of accidents i think the references may need tidying so that they are all in the exact same format ie date format etc i can do that later on if noone else does first if you have any preferences for formatting style on references or want to do it yourself please let me k

In [167]:
mytext = " ".join(mytext.split())

In [168]:
len(mytext)

59837646

In [169]:
mytext[0:1000]

'explanationwhy the edits made under my username hardcore metallica fan were reverted they were not vandalisms just closure on some gas after i voted at new york dolls fac and please do not remove the template from the talk page since i am retired now 89205 3827 daww he matches this background colour i am seemingly stuck with thanks talk 2151 january 11 2016 utc hey man i am really not trying to edit war its just that this guy is constantly removing relevant information and talking to me through edits instead of my talk page he seems to care more about the formatting than the actual info morei cannot make any real suggestions on improvement i wondered if the section statistics should be later on or a subsection of types of accidents i think the references may need tidying so that they are all in the exact same format ie date format etc i can do that later on if noone else does first if you have any preferences for formatting style on references or want to do it yourself please let me k

In [170]:
# for i in mytext:
#     print(i)

In [171]:
unicodedata.category('҈')

'Me'

In [172]:
#WORK
MARK_ENCLOSING_TABLE = dict.fromkeys(
    i for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "Me"
)
len(MARK_ENCLOSING_TABLE)

13

In [173]:
TABLE.update(MARK_ENCLOSING_TABLE)

In [174]:
mytext = mytext.translate(TABLE)

In [175]:
len(mytext)

59837642

In [176]:
mytext[0:1000]

'explanationwhy the edits made under my username hardcore metallica fan were reverted they were not vandalisms just closure on some gas after i voted at new york dolls fac and please do not remove the template from the talk page since i am retired now 89205 3827 daww he matches this background colour i am seemingly stuck with thanks talk 2151 january 11 2016 utc hey man i am really not trying to edit war its just that this guy is constantly removing relevant information and talking to me through edits instead of my talk page he seems to care more about the formatting than the actual info morei cannot make any real suggestions on improvement i wondered if the section statistics should be later on or a subsection of types of accidents i think the references may need tidying so that they are all in the exact same format ie date format etc i can do that later on if noone else does first if you have any preferences for formatting style on references or want to do it yourself please let me k

In [177]:
mytext = " ".join(mytext.split())

In [178]:
len(mytext)

59837638

In [179]:
mytext[0:1000]

'explanationwhy the edits made under my username hardcore metallica fan were reverted they were not vandalisms just closure on some gas after i voted at new york dolls fac and please do not remove the template from the talk page since i am retired now 89205 3827 daww he matches this background colour i am seemingly stuck with thanks talk 2151 january 11 2016 utc hey man i am really not trying to edit war its just that this guy is constantly removing relevant information and talking to me through edits instead of my talk page he seems to care more about the formatting than the actual info morei cannot make any real suggestions on improvement i wondered if the section statistics should be later on or a subsection of types of accidents i think the references may need tidying so that they are all in the exact same format ie date format etc i can do that later on if noone else does first if you have any preferences for formatting style on references or want to do it yourself please let me k

In [194]:
mytext = mytext.translate(str.maketrans('', '', string.punctuation))

In [214]:
string.digits

'0123456789'

In [215]:
mytext = mytext.translate(str.maketrans('', '', string.digits))


In [216]:
len(mytext)

59342990

In [217]:
mytext = " ".join(mytext.split())

In [218]:
len(mytext)

59202332

In [207]:
%%time
phrase= mytext

patterns= [r'\W+']

    
for p in patterns:
    match= re.findall(p, phrase)
#     print(match)

Wall time: 4.11 s


In [219]:
string.punctuation

'!"#$%&\'()*+,-./:;<=>?@[\\]^_`{|}~'

In [220]:
match

''

In [209]:
# mytext = mytext.translate(str.maketrans('', '', string.punctuation))

In [221]:
match = " ".join(i for i in match)

In [222]:
match = " ".join(match.split())

In [223]:
match[0:1000]

''

In [224]:
len(match)

0

In [225]:
mytext[0:1000]

'explanationwhy the edits made under my username hardcore metallica fan were reverted they were not vandalisms just closure on some gas after i voted at new york dolls fac and please do not remove the template from the talk page since i am retired now daww he matches this background colour i am seemingly stuck with thanks talk january utc hey man i am really not trying to edit war its just that this guy is constantly removing relevant information and talking to me through edits instead of my talk page he seems to care more about the formatting than the actual info morei cannot make any real suggestions on improvement i wondered if the section statistics should be later on or a subsection of types of accidents i think the references may need tidying so that they are all in the exact same format ie date format etc i can do that later on if noone else does first if you have any preferences for formatting style on references or want to do it yourself please let me knowthere appears to be a

In [226]:
len(mytext)

59202332

In [ ]:
63042228
59202332

In [227]:
words = word_tokenize(mytext)

In [235]:
'happy' in words

True

In [177]:
all_char_types = list()
for i in alltext:
    all_char_types.append(unicodedata.category(i))

In [178]:
len(all_char_types)

62829597

In [179]:
set(all_char_types)

{'Ll',
 'Lm',
 'Lo',
 'Lu',
 'Mc',
 'Me',
 'Nd',
 'Nl',
 'No',
 'Pc',
 'Pd',
 'Pe',
 'Pf',
 'Pi',
 'Po',
 'Ps',
 'Sc',
 'Sk',
 'Sm',
 'So',
 'Zl',
 'Zs'}

In [200]:
# p = string.punctuation

In [201]:
# d = list()
# for i in p:
#     d.append(unicodedata.category(i))

In [203]:
# set(d)

{'Pc', 'Pd', 'Pe', 'Po', 'Ps', 'Sc', 'Sk', 'Sm'}

In [204]:
# p

'!"#$%&\'()*+,-./:;<=>?@[\\]^_`{|}~'

In [ ]:
def char_type_preprocessing(text):
    category = unicodedata.category
    all_char_types = [category(i)a for i text]
    

In [180]:
len(alltext)

62829597

In [181]:
def cleaning_data(noizy_comment):
#     noizy_comment= re.sub(r'http\S+', '', noizy_comment)
    noizy_comment = noizy_comment.lower()
    noizy_comment = re.sub(r'\n',' ',noizy_comment)
    noizy_comment = re.sub(' +',' ',noizy_comment)
    noizy_comment = noizy_comment.strip(' ')
    cleaned_comment = noizy_comment
    return cleaned_comment


In [182]:
alltext = cleaning_data(alltext)

In [183]:
len(alltext)

62591203

In [184]:
alltext = " ".join(alltext.split())

In [185]:
len(alltext)

62586825

In [186]:
e = emoji.emoji_lis(alltext)

In [187]:
len(e)

0

In [188]:
e

[]

In [189]:
e_list = []
for i in e:
    print(i['emoji'])
    e_list.append(i['emoji'])

In [190]:
'♥' in e_list

False

In [191]:
%%time
for i in e_list:
    if i in alltext:
        alltext = alltext.replace(i, " ")

Wall time: 14.6 ms


In [168]:
# 62398330


In [192]:
len(alltext)

62586825

In [193]:
alltext = " ".join(alltext.split())

In [ ]:
62396054

In [194]:
len(alltext)

62586825

In [172]:
alltext

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.


In [195]:
alltext = cleaning_data(alltext)

In [196]:
len(alltext)

62586825

In [197]:
alltext[0:100]

'explanationwhy the edits made under my username hardcore metallica fan were reverted? they were not '

In [52]:
alltext[0:100]

"explanationwhy the edits made under my username hardcore metallica fan were reverted? they weren't v"

In [198]:
# REGEX_REPLACER = [
#     (re.compile(pat.replace("*", "\*"), flags=re.IGNORECASE), repl)
#     for pat, repl in WORDS_REPLACER
# ]
# for pattern, repl in REGEX_REPLACER:
#         alltext = pattern.sub(repl, alltext)

In [54]:
len(alltext)

62396054

In [55]:
appos = {
"aren't" : "are not",
"can't" : "cannot",
"couldn't" : "could not",
"didn't" : "did not",
"doesn't" : "does not",
"don't" : "do not",
"hadn't" : "had not",
"hasn't" : "has not",
"haven't" : "have not",
"he'd" : "he would",
"he'll" : "he will",
"he's" : "he is",
"i'd" : "I would",
"i'd" : "I had",
"i'll" : "I will",
"i'm" : "I am",
"isn't" : "is not",
"it's" : "it is",
"it'll":"it will",
"i've" : "I have",
"let's" : "let us",
"mightn't" : "might not",
"mustn't" : "must not",
"shan't" : "shall not",
"she'd" : "she would",
"she'll" : "she will",
"she's" : "she is",
"shouldn't" : "should not",
"that's" : "that is",
"there's" : "there is",
"they'd" : "they would",
"they'll" : "they will",
"they're" : "they are",
"they've" : "they have",
"we'd" : "we would",
"we're" : "we are",
"weren't" : "were not",
"we've" : "we have",
"what'll" : "what will",
"what're" : "what are",
"what's" : "what is",
"what've" : "what have",
"where's" : "where is",
"who'd" : "who would",
"who'll" : "who will",
"who're" : "who are",
"who's" : "who is",
"who've" : "who have",
"won't" : "will not",
"wouldn't" : "would not",
"you'd" : "you would",
"you'll" : "you will",
"you're" : "you are",
"you've" : "you have",
"'re": " are",
"wasn't": "was not",
"we'll":" will",
"didn't": "did not"
}

In [61]:
LOWERCASE_TABLE = {
    i: chr(i) for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "Ll"
}
len(LOWERCASE_TABLE)

2063

In [62]:
len(alltext)

62396027

In [238]:
%%time
phrase= alltext

patterns= [r'\W+']

    
for p in patterns:
    match= re.findall(p, phrase)
#     print(match)

Wall time: 4.39 s


In [239]:
match

[' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ? ',
 ' ',
 ' ',
 ' ',
 ' , ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' . ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' . ',
 '.',
 ' . ',
 '.',
 ' ',
 "'",
 ' ! ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' . ',
 ' . ( ',
 ' ) ',
 ':',
 ' , ',
 ' ',
 ' , ',
 ' ( ',
 ' ) ',
 ' ',
 ' , ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' . ',
 "'",
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' . ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' . " ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' - ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' , ',
 ' ',
 ' ',
 ' ',
 ' " " ',
 ' ',
 ' ',
 ' " " - ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',


In [201]:
mytext = ''
for i in match:
    mytext = " ".join(i)

In [202]:
mytext = ''

In [240]:
mytext = " ".join(i for i in match)

In [241]:
len(mytext)

26125004

In [194]:
mytext

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.


In [205]:
mytext = " ".join(mytext.split())

In [206]:
len(mytext)

4379539

In [197]:
mytext

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.


In [242]:
mytext[0:1000]

'                       ?         ,                           .                                 .  .  .  .   \'  !                     .   . (   )  :  ,     ,   (   )     ,                 .  \'                                          .                         . "                 -                     ,         " "       " " -                                           .             ,    -        -                                        .                                              .  \'                :   #  "   ,   ,       .                   ? "           ,         . ·   "                                     .             ,           .         \'   \'         .   ,                     (                 ) ,                                       .                             .       \'     \'                       .                   ?  .  .  .                          "           :  .        :  .  .                                                                   .                 

In [72]:
mytext = mytext.translate(str.maketrans('', '', string.punctuation))

In [73]:
len(mytext)

2104153

In [74]:
mytext[0:1000]

'                                                     ·                                                    • •                                                   • •                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    

In [243]:
mytext = " ".join(mytext.split())

In [244]:
mytext[0:1000]

'? , . . . . . \' ! . . ( ) : , , ( ) , . \' . . " - , " " " " - . , - - . . \' : # " , , . ? " , . · " . , . \' \' . , ( ) , . . \' \' . ? . . . " : . : . . . , . . , . \' \' " " " " ( ) , " " " " . , , , . . . ( • • ) : . : . . \' , . , . , , \' , . , \' , . , . / , , . : , : # . : . , , . [ ] . , . - ( : ) . . . ( • • ) " - ? ... .. @ | . ... ... , - - ( ) - ? ... , - , . , - . , - . \' . , , . , , . , . . . , . , " , , , . \' . , " " \' " " " " " " . , . , ? ? . - ( , ) . . . " ! \' , ! . : - - \' ? \' . , . ? " , : . , . . - \' \' \' \' " " . , , . ( ) " " ! " " . " " ! , " " . " " :// . . . /~ / / / . # . ( ) " " : - " " - ? \' " " . " " , . " " ; " " . , - . . . . . : ? . ? . , . , ? . " , ( ) . - . , , . , - , . , . \' . . : , ( ) " . . ? " " = = ! = = " ? , ! \' \' ? - . ] . . , - . , ( : / # . : / # : / # . ) . - :// . / / . , . " , " " " " " " " " \' . . , , . + + : / " " , . \' , , \' . , " " " " . , . , , . , ( ) , . , . " " " " " " " " \' " " " " " " . . , . " " , / . " "

In [77]:
unicodedata.category(chr('•'))

TypeError: an integer is required (got type str)

In [78]:
unicodedata.category('•')

'Po'

In [79]:
unicodedata.name('ം')

'MALAYALAM SIGN ANUSVARA'

In [80]:
bytes('☎')

TypeError: string argument without an encoding

In [81]:
unicodedata.category('☎')

'So'

In [84]:
':L' in emoticons_sad

True

In [85]:
# MORE WORK
PUNCTUATION_OTHER_TABLE = dict.fromkeys(
    i for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "Po"
)
len(PUNCTUATION_OTHER_TABLE)

544

In [86]:
TABLE.update(PUNCTUATION_OTHER_TABLE)

In [87]:
mytext = mytext.translate(TABLE)

In [88]:
len(mytext)

15860

In [89]:
mytext[0:1000]

'     「」¤  ¢ ം ാ ം ോ ോ െ ോ       ↑ ↓   ∞ ¤ ₳ ฿ ₵ ¢ ₡ ₢ ₫ ₯ € ₠ ₣ ₴ ₭ ₤ ₥ ₦ № ₧ ₰ £ ៛ ₨ ₪ ৳ ₮ ₩ ¥ − → ☓ ✰✰ ♫  → → → → ₪ ⋅ ☼ £ ⋅ ⋅  ₪  └ ┐ ¨ ¨ ¨ ¨ ¨ ¨  ♫  ≈ ≈ ⋅    → № ♪♫ ► → →    ☼   £   ¨                       ⇔ ¦ ⇒ ☿  ¢ ☥   → → → ° ☏  ¢ ✰✰      ˜      ₪  া ા ा ು ಾ ែ ा ा ொ ி ெ ு ు       ⓣ  → ← − − − − −  ♫ ♫   →     ≡ ≈ √∞ ⊕⊗ →    ♫           °                        ⁄    → ₪ →    °  ¢ →      ⁄   ₣     →    ►  → ≈ ≈ ि ी াং া ि ी াং া   ✐  → → → →  °≈→ ←≈° ♬♩ ♬ ☏    ≤        ≠ ≠      ° °  ► ° °        ∂ ╟─ ► ─╢  ∇∆∇∆     〈   −    № ♪♫  ✐   £ →    ⊕⊗ ►         ि ि   ♫                    ≠ £ £    × ×        ✄ ✄ ✄     ☻ → → ☥      ―     ► № № →    �� �� ¢    ☏ 「 『 』  」 「  」      £    ≈ ≈  £    ¢ ¢   ♫  →   ╟─ ► ─╢ ♪ ♪        ҈ ► ►   →                     → → ►  → → ≈ ≈ ♫ →     ≈ ≈      ∇∆∇∆                          £           ° °   ✆   ☇                      ⋅   →  → ← 「✎」    ← →     → ♫      ♫ ⁄  ⋅ ⋅ ⋅ ¸ ¤ °° ¤ ¸¸ ¤ °° ¤ ¸           ✽      →  ← →    ╫ ╫ 《 》  − − − − −  ∞           → № ♪♫

In [90]:
unicodedata.category('െ')

'Mc'

In [91]:
# MORE WORK
SPACING_COMBINING_TABLE = dict.fromkeys(
    i for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "Mc"
)
len(SPACING_COMBINING_TABLE)

394

In [92]:
TABLE.update(SPACING_COMBINING_TABLE)

In [93]:
mytext = mytext.translate(TABLE)

In [94]:
len(mytext)

15602

In [95]:
mytext[0:1000]

'     「」¤  ¢              ↑ ↓   ∞ ¤ ₳ ฿ ₵ ¢ ₡ ₢ ₫ ₯ € ₠ ₣ ₴ ₭ ₤ ₥ ₦ № ₧ ₰ £ ៛ ₨ ₪ ৳ ₮ ₩ ¥ − → ☓ ✰✰ ♫  → → → → ₪ ⋅ ☼ £ ⋅ ⋅  ₪  └ ┐ ¨ ¨ ¨ ¨ ¨ ¨  ♫  ≈ ≈ ⋅    → № ♪♫ ► → →    ☼   £   ¨                       ⇔ ¦ ⇒ ☿  ¢ ☥   → → → ° ☏  ¢ ✰✰      ˜      ₪                     ⓣ  → ← − − − − −  ♫ ♫   →     ≡ ≈ √∞ ⊕⊗ →    ♫           °                        ⁄    → ₪ →    °  ¢ →      ⁄   ₣     →    ►  → ≈ ≈           ✐  → → → →  °≈→ ←≈° ♬♩ ♬ ☏    ≤        ≠ ≠      ° °  ► ° °        ∂ ╟─ ► ─╢  ∇∆∇∆     〈   −    № ♪♫  ✐   £ →    ⊕⊗ ►             ♫                    ≠ £ £    × ×        ✄ ✄ ✄     ☻ → → ☥      ―     ► № № →    �� �� ¢    ☏ 「 『 』  」 「  」      £    ≈ ≈  £    ¢ ¢   ♫  →   ╟─ ► ─╢ ♪ ♪        ҈ ► ►   →                     → → ►  → → ≈ ≈ ♫ →     ≈ ≈      ∇∆∇∆                          £           ° °   ✆   ☇                      ⋅   →  → ← 「✎」    ← →     → ♫      ♫ ⁄  ⋅ ⋅ ⋅ ¸ ¤ °° ¤ ¸¸ ¤ °° ¤ ¸           ✽      →  ← →    ╫ ╫ 《 》  − − − − −  ∞           → № ♪♫   → → → → № ♪♫ £             ♫ 

In [96]:
unicodedata.category('¤')

'Sc'

In [97]:
CURRENCY_TABLE = dict.fromkeys(
    i for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "Sc"
)
len(CURRENCY_TABLE)

53

In [98]:
TABLE.update(CURRENCY_TABLE)

In [99]:
mytext = mytext.translate(TABLE)

In [100]:
len(mytext)

15203

In [101]:
mytext[0:1000]

'     「」                ↑ ↓   ∞                  №           − → ☓ ✰✰ ♫  → → → →  ⋅ ☼  ⋅ ⋅    └ ┐ ¨ ¨ ¨ ¨ ¨ ¨  ♫  ≈ ≈ ⋅    → № ♪♫ ► → →    ☼      ¨                       ⇔ ¦ ⇒ ☿   ☥   → → → ° ☏   ✰✰      ˜                           ⓣ  → ← − − − − −  ♫ ♫   →     ≡ ≈ √∞ ⊕⊗ →    ♫           °                        ⁄    →  →    °   →      ⁄        →    ►  → ≈ ≈           ✐  → → → →  °≈→ ←≈° ♬♩ ♬ ☏    ≤        ≠ ≠      ° °  ► ° °        ∂ ╟─ ► ─╢  ∇∆∇∆     〈   −    № ♪♫  ✐    →    ⊕⊗ ►             ♫                    ≠      × ×        ✄ ✄ ✄     ☻ → → ☥      ―     ► № № →    �� ��     ☏ 「 『 』  」 「  」          ≈ ≈          ♫  →   ╟─ ► ─╢ ♪ ♪        ҈ ► ►   →                     → → ►  → → ≈ ≈ ♫ →     ≈ ≈      ∇∆∇∆                                     ° °   ✆   ☇                      ⋅   →  → ← 「✎」    ← →     → ♫      ♫ ⁄  ⋅ ⋅ ⋅ ¸  °°  ¸¸  °°  ¸           ✽      →  ← →    ╫ ╫ 《 》  − − − − −  ∞           → № ♪♫   → → → → № ♪♫              ♫                           ∇∆∇∆       → → →      ⚇♔   

In [102]:
mytext = " ".join(mytext.split())

In [103]:
len(mytext)

6468

In [104]:
mytext[0:1000]

'「」 ↑ ↓ ∞ № − → ☓ ✰✰ ♫ → → → → ⋅ ☼ ⋅ ⋅ └ ┐ ¨ ¨ ¨ ¨ ¨ ¨ ♫ ≈ ≈ ⋅ → № ♪♫ ► → → ☼ ¨ ⇔ ¦ ⇒ ☿ ☥ → → → ° ☏ ✰✰ ˜ ⓣ → ← − − − − − ♫ ♫ → ≡ ≈ √∞ ⊕⊗ → ♫ ° ⁄ → → ° → ⁄ → ► → ≈ ≈ ✐ → → → → °≈→ ←≈° ♬♩ ♬ ☏ ≤ ≠ ≠ ° ° ► ° ° ∂ ╟─ ► ─╢ ∇∆∇∆ 〈 − № ♪♫ ✐ → ⊕⊗ ► ♫ ≠ × × ✄ ✄ ✄ ☻ → → ☥ ― ► № № → �� �� ☏ 「 『 』 」 「 」 ≈ ≈ ♫ → ╟─ ► ─╢ ♪ ♪ ҈ ► ► → → → ► → → ≈ ≈ ♫ → ≈ ≈ ∇∆∇∆ ° ° ✆ ☇ ⋅ → → ← 「✎」 ← → → ♫ ♫ ⁄ ⋅ ⋅ ⋅ ¸ °° ¸¸ °° ¸ ✽ → ← → ╫ ╫ 《 》 − − − − − ∞ → № ♪♫ → → → → № ♪♫ ♫ ∇∆∇∆ → → → ⚇♔ ㎥ − → ☼ ► ► → ● ✓ ☥ ► → ♫♫ ☥ → ☭ ☭ ∀ ♬ → ➥ ♫ → → ≠ → ⋅ ← → ♪♫ ≠ ✎ ◕‿◕ ¦ ♪♫ 「 」 → ✽ → × → ⁄ → ► ♪♫ ► ♪♫ ► ♪♫ ← → ℥ ☏ ۩ ۞ ← → ← ► ← → ☏ ♝♚ ✄ ✄ ✄ ⇔ ¦ ⇒ → ⇔ ¦ ⇒ ☏ ☛ ― → ◅ ► → ← ♫♫ ➔ ♫ ♫ ☥ ¨ ☼ ► → ⇔ ← ─ ⊕⊗ ● ✓ → → ♪ ♫ °° ≈ ≈ ↓ ✄ ✄ ✄ ← → → → → → → → ˜ ∇∆∇∆ ← → ► ― ← ☼ ≈ → → ╟─► ─╢ ⊕ ➨ ¬ ∇∆∇∆ ⇔ ¦ ⇒ ➪ ← → ˺ → ← → ♫ ° ° ° ⁄ ← ☏ ☏ ≠ − ÷ → → → ⇔ → ♪♫ ← ← ← ← ° → ← ← → → → → → → → ↓ − − − − − − → ✽ − → ♬♩ ∇∆∇∆ ¦ ► ¦ → →← ← ♫ ℠ → ← → ► ♪♫ ► ° ← → ☼ ✽ → ✽ ☼ → ● ∇∆∇∆ � °° ← → ∙ → ¯ ¯ ¯ ¯¯¸ ¨¯ ¯ ¯ ¯ ¯¯¸ ¨¯ → ≈ ≈ ↑ ▎ 《 》 ° → ← ✿ ∅ → ☻ ☼ → × ≈ → ‑ − №

In [105]:
unicodedata.category('」')

'Pe'

In [106]:
PUNCTUATION_CLOSE_TABLE = dict.fromkeys(
    i for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "Pe"
)
len(PUNCTUATION_CLOSE_TABLE)

73

In [107]:
TABLE.update(PUNCTUATION_CLOSE_TABLE)

In [108]:
mytext = mytext.translate(TABLE)

In [109]:
len(mytext)

6437

In [110]:
mytext[0:1000]

'「 ↑ ↓ ∞ № − → ☓ ✰✰ ♫ → → → → ⋅ ☼ ⋅ ⋅ └ ┐ ¨ ¨ ¨ ¨ ¨ ¨ ♫ ≈ ≈ ⋅ → № ♪♫ ► → → ☼ ¨ ⇔ ¦ ⇒ ☿ ☥ → → → ° ☏ ✰✰ ˜ ⓣ → ← − − − − − ♫ ♫ → ≡ ≈ √∞ ⊕⊗ → ♫ ° ⁄ → → ° → ⁄ → ► → ≈ ≈ ✐ → → → → °≈→ ←≈° ♬♩ ♬ ☏ ≤ ≠ ≠ ° ° ► ° ° ∂ ╟─ ► ─╢ ∇∆∇∆ 〈 − № ♪♫ ✐ → ⊕⊗ ► ♫ ≠ × × ✄ ✄ ✄ ☻ → → ☥ ― ► № № → �� �� ☏ 「 『   「  ≈ ≈ ♫ → ╟─ ► ─╢ ♪ ♪ ҈ ► ► → → → ► → → ≈ ≈ ♫ → ≈ ≈ ∇∆∇∆ ° ° ✆ ☇ ⋅ → → ← 「✎ ← → → ♫ ♫ ⁄ ⋅ ⋅ ⋅ ¸ °° ¸¸ °° ¸ ✽ → ← → ╫ ╫ 《  − − − − − ∞ → № ♪♫ → → → → № ♪♫ ♫ ∇∆∇∆ → → → ⚇♔ ㎥ − → ☼ ► ► → ● ✓ ☥ ► → ♫♫ ☥ → ☭ ☭ ∀ ♬ → ➥ ♫ → → ≠ → ⋅ ← → ♪♫ ≠ ✎ ◕‿◕ ¦ ♪♫ 「  → ✽ → × → ⁄ → ► ♪♫ ► ♪♫ ► ♪♫ ← → ℥ ☏ ۩ ۞ ← → ← ► ← → ☏ ♝♚ ✄ ✄ ✄ ⇔ ¦ ⇒ → ⇔ ¦ ⇒ ☏ ☛ ― → ◅ ► → ← ♫♫ ➔ ♫ ♫ ☥ ¨ ☼ ► → ⇔ ← ─ ⊕⊗ ● ✓ → → ♪ ♫ °° ≈ ≈ ↓ ✄ ✄ ✄ ← → → → → → → → ˜ ∇∆∇∆ ← → ► ― ← ☼ ≈ → → ╟─► ─╢ ⊕ ➨ ¬ ∇∆∇∆ ⇔ ¦ ⇒ ➪ ← → ˺ → ← → ♫ ° ° ° ⁄ ← ☏ ☏ ≠ − ÷ → → → ⇔ → ♪♫ ← ← ← ← ° → ← ← → → → → → → → ↓ − − − − − − → ✽ − → ♬♩ ∇∆∇∆ ¦ ► ¦ → →← ← ♫ ℠ → ← → ► ♪♫ ► ° ← → ☼ ✽ → ✽ ☼ → ● ∇∆∇∆ � °° ← → ∙ → ¯ ¯ ¯ ¯¯¸ ¨¯ ¯ ¯ ¯ ¯¯¸ ¨¯ → ≈ ≈ ↑ ▎ 《  ° → ← ✿ ∅ → ☻ ☼ → × ≈ → ‑ − № ♪♫ × → 

In [111]:
mytext = " ".join(mytext.split())

In [112]:
len(mytext)

6411

In [113]:
unicodedata.category('「')

'Ps'

In [114]:
PUNCTUATION_OPEN_TABLE = dict.fromkeys(
    i for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "Ps"
)
len(PUNCTUATION_OPEN_TABLE)

75

In [115]:
TABLE.update(PUNCTUATION_OPEN_TABLE)

In [116]:
mytext = mytext.translate(TABLE)

In [117]:
len(mytext)

6340

In [118]:
mytext[0:1000]

' ↑ ↓ ∞ № − → ☓ ✰✰ ♫ → → → → ⋅ ☼ ⋅ ⋅ └ ┐ ¨ ¨ ¨ ¨ ¨ ¨ ♫ ≈ ≈ ⋅ → № ♪♫ ► → → ☼ ¨ ⇔ ¦ ⇒ ☿ ☥ → → → ° ☏ ✰✰ ˜ ⓣ → ← − − − − − ♫ ♫ → ≡ ≈ √∞ ⊕⊗ → ♫ ° ⁄ → → ° → ⁄ → ► → ≈ ≈ ✐ → → → → °≈→ ←≈° ♬♩ ♬ ☏ ≤ ≠ ≠ ° ° ► ° ° ∂ ╟─ ► ─╢ ∇∆∇∆  − № ♪♫ ✐ → ⊕⊗ ► ♫ ≠ × × ✄ ✄ ✄ ☻ → → ☥ ― ► № № → �� �� ☏    ≈ ≈ ♫ → ╟─ ► ─╢ ♪ ♪ ҈ ► ► → → → ► → → ≈ ≈ ♫ → ≈ ≈ ∇∆∇∆ ° ° ✆ ☇ ⋅ → → ← ✎ ← → → ♫ ♫ ⁄ ⋅ ⋅ ⋅ ¸ °° ¸¸ °° ¸ ✽ → ← → ╫ ╫  − − − − − ∞ → № ♪♫ → → → → № ♪♫ ♫ ∇∆∇∆ → → → ⚇♔ ㎥ − → ☼ ► ► → ● ✓ ☥ ► → ♫♫ ☥ → ☭ ☭ ∀ ♬ → ➥ ♫ → → ≠ → ⋅ ← → ♪♫ ≠ ✎ ◕‿◕ ¦ ♪♫  → ✽ → × → ⁄ → ► ♪♫ ► ♪♫ ► ♪♫ ← → ℥ ☏ ۩ ۞ ← → ← ► ← → ☏ ♝♚ ✄ ✄ ✄ ⇔ ¦ ⇒ → ⇔ ¦ ⇒ ☏ ☛ ― → ◅ ► → ← ♫♫ ➔ ♫ ♫ ☥ ¨ ☼ ► → ⇔ ← ─ ⊕⊗ ● ✓ → → ♪ ♫ °° ≈ ≈ ↓ ✄ ✄ ✄ ← → → → → → → → ˜ ∇∆∇∆ ← → ► ― ← ☼ ≈ → → ╟─► ─╢ ⊕ ➨ ¬ ∇∆∇∆ ⇔ ¦ ⇒ ➪ ← → ˺ → ← → ♫ ° ° ° ⁄ ← ☏ ☏ ≠ − ÷ → → → ⇔ → ♪♫ ← ← ← ← ° → ← ← → → → → → → → ↓ − − − − − − → ✽ − → ♬♩ ∇∆∇∆ ¦ ► ¦ → →← ← ♫ ℠ → ← → ► ♪♫ ► ° ← → ☼ ✽ → ✽ ☼ → ● ∇∆∇∆ � °° ← → ∙ → ¯ ¯ ¯ ¯¯¸ ¨¯ ¯ ¯ ¯ ¯¯¸ ¨¯ → ≈ ≈ ↑ ▎  ° → ← ✿ ∅ → ☻ ☼ → × ≈ → ‑ − № ♪♫ × → → → → → → → ► －

In [119]:
mytext = " ".join(mytext.split())

In [120]:
len(mytext)

6274

In [121]:
unicodedata.category('↑')

'Sm'

In [122]:
SYMBOL_MATH_TABLE = dict.fromkeys(
    i for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "Sm"
)
len(SYMBOL_MATH_TABLE)

948

In [123]:
TABLE.update(SYMBOL_MATH_TABLE)

In [124]:
mytext = mytext.translate(TABLE)

In [125]:
len(mytext)

4601

In [128]:
TweetTokenizer().tokenize('◕‿◕')

['◕', '‿', '◕']

In [129]:
mytext[0:1000]

'   №   ☓ ✰✰ ♫      ☼   └ ┐ ¨ ¨ ¨ ¨ ¨ ¨ ♫     № ♪♫ ►   ☼ ¨  ¦  ☿ ☥    ° ☏ ✰✰ ˜ ⓣ        ♫ ♫       ♫ °    °    ►    ✐     ° ° ♬♩ ♬ ☏    ° ° ► ° °  ╟─ ► ─╢   № ♪♫ ✐   ► ♫    ✄ ✄ ✄ ☻   ☥ ― ► № №  �� �� ☏   ♫  ╟─ ► ─╢ ♪ ♪ ҈ ► ►    ►     ♫     ° ° ✆ ☇     ✎    ♫ ♫     ¸ °° ¸¸ °° ¸ ✽    ╫ ╫        № ♪♫     № ♪♫ ♫     ⚇♔ ㎥   ☼ ► ►  ● ✓ ☥ ►  ♫♫ ☥  ☭ ☭  ♬  ➥ ♫        ♪♫  ✎ ◕‿◕ ¦ ♪♫  ✽      ► ♪♫ ► ♪♫ ► ♪♫   ℥ ☏ ۩ ۞    ►   ☏ ♝♚ ✄ ✄ ✄  ¦    ¦  ☏ ☛ ―  ◅ ►   ♫♫ ➔ ♫ ♫ ☥ ¨ ☼ ►    ─  ● ✓   ♪ ♫ °°    ✄ ✄ ✄         ˜    ► ―  ☼    ╟─► ─╢  ➨    ¦  ➪   ˺    ♫ ° ° °   ☏ ☏         ♪♫     °                   ✽   ♬♩  ¦ ► ¦    ♫ ℠    ► ♪♫ ► °   ☼ ✽  ✽ ☼  ●  � °°     ¯ ¯ ¯ ¯¯¸ ¨¯ ¯ ¯ ¯ ¯¯¸ ¨¯     ▎ °   ✿   ☻ ☼     ‑  № ♪♫         ► － °  ― °° °° ► ° ✎        ☏  ► ♪♫  ¦ ◕‿◕ ►     ✽ ► ♪♫ ☼  ╟─ ► ─╢   ☼ └ ┐ ☼ └ ┐   ᾽ ᾽ ᾽ ᾽ ᾽     ✄ ✄ ✄ ✄ ✄ ✄ ╟─ ► ─╢  ♫♫ ♫♫   ☥ ► ♪♫ ♪♫ ° ° °   ► ―   ➨      ☏ ¦ ♪ ♪       ►  ☼ ╟─ ► ─╢ ◕‿◕ ⚇♔    ‹ ›‹ ›  ― ― ☥ ◕‿◕        ‹›  ► °  ► ☏ ►       ♪ ♫ ☥  ► ☼  ⚇♔    ☞ ☜ ► ―    ► └┘┌ ┐  ☼ °° ► ♪♫ 

In [130]:
mytext = " ".join(mytext.split())

In [131]:
len(mytext)

3137

In [132]:
unicodedata.category('№')

'So'

In [133]:
#WORK
SYMBOL_OTHER_TABLE = dict.fromkeys(
    i for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "So"
)
len(SYMBOL_OTHER_TABLE)

5777

In [134]:
TABLE.update(SYMBOL_OTHER_TABLE)

In [135]:
mytext = mytext.translate(TABLE)

In [136]:
len(mytext)

1553

In [137]:
mytext[0:1000]

'       ¨ ¨ ¨ ¨ ¨ ¨      ¨       ˜                                ―             ҈            ¸  ¸¸  ¸                           ‿                        ―        ¨            ˜  ―       ˺                           ¯ ¯ ¯ ¯¯¸ ¨¯ ¯ ¯ ¯ ¯¯¸ ¨¯      ‑    －  ―          ‿               ᾽ ᾽ ᾽ ᾽ ᾽                    ―           ‿  ‹ ›‹ › ― ―  ‿ ‹›               ―                                         ―  ¯ ¯ ¯¯¯¸ ¨¯ ¯                  ―                                                   ‒    ¯ ¯ ¯ ¯¯¸ ¨¯ ¯ ¯ ¯ ¯¯¸ ¨¯   ‹  ›                                     ‿  ‿                    ―          ―               ―                                                ‿                   ‿ ˜˜˜˜  ―                                  ¯ ¯ ¯ ¯¯¸ ¨¯ ¯ ¯ ¯ ¯¯¸ ¨¯         ―                                             ― ‹›                                                ¨¨¨¨                                    ‿                     ‿               ‿             ¯ ¯ ¯ ¯¯¸ ¨¯ ¯ ¯ ¯ ¯¯¸ ¨¯   ‿             ¨    ―        

In [138]:
mytext = " ".join(mytext.split())

In [139]:
len(mytext)

350

In [140]:
unicodedata.category('´')

'Sk'

In [141]:
#WORK
SYMBOL_MODIFIER_TABLE = dict.fromkeys(
    i for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "Sk"
)
len(SYMBOL_MODIFIER_TABLE)

121

In [142]:
TABLE.update(SYMBOL_MODIFIER_TABLE)

In [143]:
mytext = mytext.translate(TABLE)

In [144]:
len(mytext)

227

In [145]:
mytext[0:1000]

'        ― ҈    ‿ ―   ―            ‑ － ― ‿      ― ‿ ‹ ›‹ › ― ― ‿ ‹› ― ―      ― ‒           ‹ › ‿ ‿ ― ― ― ‿ ‿  ―           ― ― ‹›  ‿ ‿ ‿           ‿  ― ―  ―  ‿ ―   ‿ ‿ ― ― ‑ ―― ― ‒  ‿ ‿ ‿      ҈ ― ―   ― ‐ ‐ ―  ― ‹› ҈ ҉ ‹› ‑‑  ― ‿'

In [146]:
mytext = " ".join(mytext.split())

In [147]:
len(mytext)

146

In [148]:
mytext[0:1000]

'― ҈ ‿ ― ― ‑ － ― ‿ ― ‿ ‹ ›‹ › ― ― ‿ ‹› ― ― ― ‒ ‹ › ‿ ‿ ― ― ― ‿ ‿ ― ― ― ‹› ‿ ‿ ‿ ‿ ― ― ― ‿ ― ‿ ‿ ― ― ‑ ―― ― ‒ ‿ ‿ ‿ ҈ ― ― ― ‐ ‐ ― ― ‹› ҈ ҉ ‹› ‑‑ ― ‿'

In [149]:
unicodedata.category('―')

'Pd'

In [150]:
#WORK
PUNCTUATION_DASH_TABLE = dict.fromkeys(
    i for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "Pd"
)
len(PUNCTUATION_DASH_TABLE)

24

In [151]:
TABLE.update(PUNCTUATION_DASH_TABLE)

In [152]:
mytext = mytext.translate(TABLE)

In [153]:
len(mytext)

106

In [154]:
mytext[0:1000]

' ҈ ‿      ‿  ‿ ‹ ›‹ ›   ‿ ‹›     ‹ › ‿ ‿    ‿ ‿    ‹› ‿ ‿ ‿ ‿    ‿  ‿ ‿       ‿ ‿ ‿ ҈        ‹› ҈ ҉ ‹›   ‿'

In [155]:
mytext = " ".join(mytext.split())

In [156]:
len(mytext)

68

In [157]:
mytext[0:1000]

'҈ ‿ ‿ ‿ ‹ ›‹ › ‿ ‹› ‹ › ‿ ‿ ‿ ‿ ‹› ‿ ‿ ‿ ‿ ‿ ‿ ‿ ‿ ‿ ‿ ҈ ‹› ҈ ҉ ‹› ‿'

In [158]:
unicodedata.category('‿')

'Pc'

In [159]:
#WORK
PUNCTUATION_CONNECTOR_TABLE = dict.fromkeys(
    i for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "Pc"
)
len(PUNCTUATION_CONNECTOR_TABLE)

10

In [160]:
TABLE.update(PUNCTUATION_CONNECTOR_TABLE)

In [161]:
mytext = mytext.translate(TABLE)

In [162]:
len(mytext)

49

In [163]:
mytext[0:1000]

'҈    ‹ ›‹ ›  ‹› ‹ ›     ‹›           ҈ ‹› ҈ ҉ ‹› '

In [164]:
mytext = " ".join(mytext.split())

In [165]:
len(mytext)

30

In [166]:
mytext[0:1000]

'҈ ‹ ›‹ › ‹› ‹ › ‹› ҈ ‹› ҈ ҉ ‹›'

In [167]:
unicodedata.category('›')

'Pf'

In [168]:
#WORK
PUNCTUATION_FINAL_QUOTE_TABLE = dict.fromkeys(
    i for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "Pf"
)
len(PUNCTUATION_FINAL_QUOTE_TABLE)

10

In [169]:
TABLE.update(PUNCTUATION_FINAL_QUOTE_TABLE)

In [170]:
mytext = mytext.translate(TABLE)

In [171]:
len(mytext)

23

In [172]:
mytext[0:1000]

'҈ ‹ ‹  ‹ ‹  ‹ ҈ ‹ ҈ ҉ ‹'

In [173]:
mytext = " ".join(mytext.split())

In [174]:
len(mytext)

21

In [175]:
mytext[0:1000]

'҈ ‹ ‹ ‹ ‹ ‹ ҈ ‹ ҈ ҉ ‹'

In [176]:
unicodedata.category('‹')

'Pi'

In [177]:
#WORK
PUNCTUATION_INITIAL_QUOTE_TABLE = dict.fromkeys(
    i for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "Pi"
)
len(PUNCTUATION_INITIAL_QUOTE_TABLE)

12

In [178]:
TABLE.update(PUNCTUATION_INITIAL_QUOTE_TABLE)

In [179]:
mytext = mytext.translate(TABLE)

In [180]:
len(mytext)

14

In [181]:
mytext[0:1000]

'҈      ҈  ҈ ҉ '

In [182]:
mytext = " ".join(mytext.split())

In [183]:
len(mytext)

7

In [184]:
mytext[0:1000]

'҈ ҈ ҈ ҉'

In [185]:
for i in mytext:
    print(i)

҈
 
҈
 
҈
 
҉


In [186]:
unicodedata.category('҈')

'Me'

In [187]:
#WORK
MARK_ENCLOSING_TABLE = dict.fromkeys(
    i for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "Me"
)
len(MARK_ENCLOSING_TABLE)

13

In [188]:
TABLE.update(MARK_ENCLOSING_TABLE)

In [189]:
mytext = mytext.translate(TABLE)

In [190]:
len(mytext)

3

In [191]:
mytext[0:1000]

'   '

In [192]:
mytext = " ".join(mytext.split())

In [193]:
len(mytext)

0

In [194]:
mytext[0:1000]

''

In [33]:
emoji.emoji_lis(alltext)

[{'emoji': '↔', 'location': 49928},
 {'emoji': '♠', 'location': 50041},
 {'emoji': '♣', 'location': 50043},
 {'emoji': '♥', 'location': 50045},
 {'emoji': '♦', 'location': 50047},
 {'emoji': '™', 'location': 57263},
 {'emoji': '☎', 'location': 61062},
 {'emoji': '♥', 'location': 79993},
 {'emoji': '♥', 'location': 79994},
 {'emoji': '♥', 'location': 80001},
 {'emoji': '♥', 'location': 80002},
 {'emoji': '♠', 'location': 151051},
 {'emoji': '♥', 'location': 151052},
 {'emoji': '♦', 'location': 151053},
 {'emoji': '♣', 'location': 151054},
 {'emoji': '🗽', 'location': 158102},
 {'emoji': '☎', 'location': 236543},
 {'emoji': '♦', 'location': 265960},
 {'emoji': '♥', 'location': 293734},
 {'emoji': '♥', 'location': 293735},
 {'emoji': '♥', 'location': 293736},
 {'emoji': '♥', 'location': 293737},
 {'emoji': '♥', 'location': 293738},
 {'emoji': '♥', 'location': 293739},
 {'emoji': '♥', 'location': 293740},
 {'emoji': '♥', 'location': 293741},
 {'emoji': '♥', 'location': 293742},
 {'emoji': '

In [34]:
alltext[49928]

'↔'

In [52]:
unicodedata.normalize("NFKD", 'Hrll')

'Hrll'

In [53]:
emoji.UNICODE_EMOJI_ALIAS.items()

dict_items([('🥇', ':1st_place_medal:'), ('🥈', ':2nd_place_medal:'), ('🥉', ':3rd_place_medal:'), ('🆎', ':ab:'), ('🏧', ':atm:'), ('🅰', ':a:'), ('🇦🇫', ':flag_for_Afghanistan:'), ('🇦🇱', ':flag_for_Albania:'), ('🇩🇿', ':flag_for_Algeria:'), ('🇦🇸', ':flag_for_American_Samoa:'), ('🇦🇩', ':flag_for_Andorra:'), ('🇦🇴', ':flag_for_Angola:'), ('🇦🇮', ':flag_for_Anguilla:'), ('🇦🇶', ':flag_for_Antarctica:'), ('🇦🇬', ':flag_for_Antigua_&_Barbuda:'), ('♒', ':aquarius:'), ('🇦🇷', ':flag_for_Argentina:'), ('♈', ':aries:'), ('🇦🇲', ':flag_for_Armenia:'), ('🇦🇼', ':flag_for_Aruba:'), ('🇦🇨', ':flag_for_Ascension_Island:'), ('🇦🇺', ':flag_for_Australia:'), ('🇦🇹', ':flag_for_Austria:'), ('🇦🇿', ':flag_for_Azerbaijan:'), ('🔙', ':back:'), ('🅱', ':b:'), ('🇧🇸', ':flag_for_Bahamas:'), ('🇧🇭', ':flag_for_Bahrain:'), ('🇧🇩', ':flag_for_Bangladesh:'), ('🇧🇧', ':flag_for_Barbados:'), ('🇧🇾', ':flag_for_Belarus:'), ('🇧🇪', ':flag_for_Belgium:'), ('🇧🇿', ':flag_for_Belize:'), ('🇧🇯', ':flag_for_Benin:'), ('🇧🇲', ':flag_for_Bermuda:'), 

In [54]:
UNICODE_EMOJI_MY = {
    k: f" EMJ {v.strip(':').replace('_', ' ')} "
    for k, v in emoji.UNICODE_EMOJI_ALIAS.items()
}

In [55]:
UNICODE_EMOJI_MY

{'🥇': ' EMJ 1st place medal ',
 '🥈': ' EMJ 2nd place medal ',
 '🥉': ' EMJ 3rd place medal ',
 '🆎': ' EMJ ab ',
 '🏧': ' EMJ atm ',
 '🅰': ' EMJ a ',
 '🇦🇫': ' EMJ flag for Afghanistan ',
 '🇦🇱': ' EMJ flag for Albania ',
 '🇩🇿': ' EMJ flag for Algeria ',
 '🇦🇸': ' EMJ flag for American Samoa ',
 '🇦🇩': ' EMJ flag for Andorra ',
 '🇦🇴': ' EMJ flag for Angola ',
 '🇦🇮': ' EMJ flag for Anguilla ',
 '🇦🇶': ' EMJ flag for Antarctica ',
 '🇦🇬': ' EMJ flag for Antigua & Barbuda ',
 '♒': ' EMJ aquarius ',
 '🇦🇷': ' EMJ flag for Argentina ',
 '♈': ' EMJ aries ',
 '🇦🇲': ' EMJ flag for Armenia ',
 '🇦🇼': ' EMJ flag for Aruba ',
 '🇦🇨': ' EMJ flag for Ascension Island ',
 '🇦🇺': ' EMJ flag for Australia ',
 '🇦🇹': ' EMJ flag for Austria ',
 '🇦🇿': ' EMJ flag for Azerbaijan ',
 '🔙': ' EMJ back ',
 '🅱': ' EMJ b ',
 '🇧🇸': ' EMJ flag for Bahamas ',
 '🇧🇭': ' EMJ flag for Bahrain ',
 '🇧🇩': ' EMJ flag for Bangladesh ',
 '🇧🇧': ' EMJ flag for Barbados ',
 '🇧🇾': ' EMJ flag for Belarus ',
 '🇧🇪': ' EMJ flag for Belgium ',
 '🇧

In [57]:
UNICODE_EMOJI_MY.get('match'.group(0), 'match'.group(0))

AttributeError: 'str' object has no attribute 'group'

In [179]:
appos = {
"aren't" : "are not",
"can't" : "cannot",
"couldn't" : "could not",
"didn't" : "did not",
"doesn't" : "does not",
"don't" : "do not",
"hadn't" : "had not",
"hasn't" : "has not",
"haven't" : "have not",
"he'd" : "he would",
"he'll" : "he will",
"he's" : "he is",
"i'd" : "I would",
"i'd" : "I had",
"i'll" : "I will",
"i'm" : "I am",
"isn't" : "is not",
"it's" : "it is",
"it'll":"it will",
"i've" : "I have",
"let's" : "let us",
"mightn't" : "might not",
"mustn't" : "must not",
"shan't" : "shall not",
"she'd" : "she would",
"she'll" : "she will",
"she's" : "she is",
"shouldn't" : "should not",
"that's" : "that is",
"there's" : "there is",
"they'd" : "they would",
"they'll" : "they will",
"they're" : "they are",
"they've" : "they have",
"we'd" : "we would",
"we're" : "we are",
"weren't" : "were not",
"we've" : "we have",
"what'll" : "what will",
"what're" : "what are",
"what's" : "what is",
"what've" : "what have",
"where's" : "where is",
"who'd" : "who would",
"who'll" : "who will",
"who're" : "who are",
"who's" : "who is",
"who've" : "who have",
"won't" : "will not",
"wouldn't" : "would not",
"you'd" : "you would",
"you'll" : "you will",
"you're" : "you are",
"you've" : "you have",
"'re": " are",
"wasn't": "was not",
"we'll":" will",
"didn't": "did not"
}

In [2]:
goodwords_replacer = {"ain't": "is not", "aren't": "are not","can't": "cannot", "'cause": "because", 
                       "could've": "could have", "couldn't": "could not", "didn't": "did not",  "doesn't": "does not", 
                       "don't": "do not", "hadn't": "had not", "hasn't": "has not", "haven't": "have not", "he'd": "he would",
                       "he'll": "he will", "he's": "he is", "how'd": "how did", "how'd'y": "how do you", "how'll": "how will", 
                       "how's": "how is",  "I'd": "I would", "I'd've": "I would have", "I'll": "I will",
                       "I'll've": "I will have","I'm": "I am", "I've": "I have", "i'd": "i would", "i'd've": "i would have", 
                       "i'll": "i will",  "i'll've": "i will have","i'm": "i am", "i've": "i have", "isn't": "is not", 
                       "it'd": "it would", "it'd've": "it would have", "it'll": "it will", "it'll've": "it will have",
                       "it's": "it is", "let's": "let us", "ma'am": "madam", "mayn't": "may not", "might've": "might have",
                       "mightn't": "might not","mightn't've": "might not have", "must've": "must have", 
                       "mustn't": "must not", "mustn't've": "must not have", "needn't": "need not", 
                       "needn't've": "need not have","o'clock": "of the clock", "oughtn't": "ought not", 
                       "oughtn't've": "ought not have", "shan't": "shall not", "sha'n't": "shall not", 
                       "shan't've": "shall not have", "she'd": "she would", "she'd've": "she would have", 
                       "she'll": "she will", "she'll've": "she will have", "she's": "she is", "should've": "should have", 
                       "shouldn't": "should not", "shouldn't've": "should not have", "so've": "so have","so's": "so as", 
                       "this's": "this is","that'd": "that would", "that'd've": "that would have", "that's": "that is", 
                       "there'd": "there would", "there'd've": "there would have", "there's": "there is", 
                       "here's": "here is","they'd": "they would", "they'd've": "they would have", 
                       "they'll": "they will", "they'll've": "they will have", "they're": "they are", 
                       "they've": "they have", "to've": "to have", "wasn't": "was not", "we'd": "we would", 
                       "we'd've": "we would have", "we'll": "we will", "we'll've": "we will have", "we're": "we are", 
                       "we've": "we have", "weren't": "were not", "what'll": "what will", "what'll've": "what will have", 
                       "what're": "what are",  "what's": "what is", "what've": "what have", 
                       "when's": "when is", "when've": "when have", "where'd": "where did", "where's": "where is", 
                       "where've": "where have", "who'll": "who will", "who'll've": "who will have", 
                       "who's": "who is", "who've": "who have", "why's": "why is", "why've": "why have", 
                       "will've": "will have", "won't": "will not", "won't've": "will not have", "would've": "would have", 
                       "wouldn't": "would not", "wouldn't've": "would not have", "y'all": "you all", 
                       "y'all'd": "you all would","y'all'd've": "you all would have","y'all're": "you all are",
                       "y'all've": "you all have","you'd": "you would", "you'd've": "you would have", "you'll": "you will", 
                       "you'll've": "you will have", "you're": "you are", "you've": "you have" }

In [3]:
symbols_to_isolate = '.,?!-;*"…:—()%#$&_/@＼・ω+=”“[]^–>\\°<~•≠™ˈʊɒ∞§{}·τα❤☺ɡ|¢→̶`❥━┣┫┗Ｏ►★©―ɪ✔®\x96\x92●£♥➤´¹☕≈÷♡◐║▬′ɔː€۩۞†μ✒➥═☆ˌ◄½ʻπδηλσερνʃ✬ＳＵＰＥＲＩＴ☻±♍µº¾✓◾؟．⬅℅»Вав❣⋅¿¬♫ＣＭβ█▓▒░⇒⭐›¡₂₃❧▰▔◞▀▂▃▄▅▆▇↙γ̄″☹➡«φ⅓„✋：¥̲̅́∙‛◇✏▷❓❗¶˚˙）сиʿ✨。ɑ\x80◕！％¯−ﬂﬁ₁²ʌ¼⁴⁄₄⌠♭✘╪▶☭✭♪☔☠♂☃☎✈✌✰❆☙○‣⚓年∎ℒ▪▙☏⅛ｃａｓǀ℮¸ｗ‚∼‖ℳ❄←☼⋆ʒ⊂、⅔¨͡๏⚾⚽Φ×θ￦？（℃⏩☮⚠月✊❌⭕▸■⇌☐☑⚡☄ǫ╭∩╮，例＞ʕɐ̣Δ₀✞┈╱╲▏▕┃╰▊▋╯┳┊≥☒↑☝ɹ✅☛♩☞ＡＪＢ◔◡↓♀⬆̱ℏ\x91⠀ˤ╚↺⇤∏✾◦♬³の｜／∵∴√Ω¤☜▲↳▫‿⬇✧ｏｖｍ－２０８＇‰≤∕ˆ⚜☁'
symbols_to_delete = '\n🍕\r🐵😑\xa0\ue014\t\uf818\uf04a\xad😢🐶️\uf0e0😜😎👊\u200b\u200e😁عدويهصقأناخلىبمغر😍💖💵Е👎😀😂\u202a\u202c🔥😄🏻💥ᴍʏʀᴇɴᴅᴏᴀᴋʜᴜʟᴛᴄᴘʙғᴊᴡɢ😋👏שלוםבי😱‼\x81エンジ故障\u2009🚌ᴵ͞🌟😊😳😧🙀😐😕\u200f👍😮😃😘אעכח💩💯⛽🚄🏼ஜ😖ᴠ🚲‐😟😈💪🙏🎯🌹😇💔😡\x7f👌ἐὶήιὲκἀίῃἴξ🙄Ｈ😠\ufeff\u2028😉😤⛺🙂\u3000تحكسة👮💙فزط😏🍾🎉😞\u2008🏾😅😭👻😥😔😓🏽🎆🍻🍽🎶🌺🤔😪\x08‑🐰🐇🐱🙆😨🙃💕𝘊𝘦𝘳𝘢𝘵𝘰𝘤𝘺𝘴𝘪𝘧𝘮𝘣💗💚地獄谷улкнПоАН🐾🐕😆ה🔗🚽歌舞伎🙈😴🏿🤗🇺🇸мυтѕ⤵🏆🎃😩\u200a🌠🐟💫💰💎эпрд\x95🖐🙅⛲🍰🤐👆🙌\u2002💛🙁👀🙊🙉\u2004ˢᵒʳʸᴼᴷᴺʷᵗʰᵉᵘ\x13🚬🤓\ue602😵άοόςέὸתמדףנרךצט😒͝🆕👅👥👄🔄🔤👉👤👶👲🔛🎓\uf0b7\uf04c\x9f\x10成都😣⏺😌🤑🌏😯ех😲Ἰᾶὁ💞🚓🔔📚🏀👐\u202d💤🍇\ue613小土豆🏡❔⁉\u202f👠》कर्मा🇹🇼🌸蔡英文🌞🎲レクサス😛外国人关系Сб💋💀🎄💜🤢َِьыгя不是\x9c\x9d🗑\u2005💃📣👿༼つ༽😰ḷЗз▱ц￼🤣卖温哥华议会下降你失去所有的钱加拿大坏税骗子🐝ツ🎅\x85🍺آإشء🎵🌎͟ἔ油别克🤡🤥😬🤧й\u2003🚀🤴ʲшчИОРФДЯМюж😝🖑ὐύύ特殊作戦群щ💨圆明园קℐ🏈😺🌍⏏ệ🍔🐮🍁🍆🍑🌮🌯🤦\u200d𝓒𝓲𝓿𝓵안영하세요ЖљКћ🍀😫🤤ῦ我出生在了可以说普通话汉语好极🎼🕺🍸🥂🗽🎇🎊🆘🤠👩🖒🚪天一家⚲\u2006⚭⚆⬭⬯⏖新✀╌🇫🇷🇩🇪🇮🇬🇧😷🇨🇦ХШ🌐\x1f杀鸡给猴看ʁ𝗪𝗵𝗲𝗻𝘆𝗼𝘂𝗿𝗮𝗹𝗶𝘇𝗯𝘁𝗰𝘀𝘅𝗽𝘄𝗱📺ϖ\u2000үսᴦᎥһͺ\u2007հ\u2001ɩｙｅ൦ｌƽｈ𝐓𝐡𝐞𝐫𝐮𝐝𝐚𝐃𝐜𝐩𝐭𝐢𝐨𝐧Ƅᴨןᑯ໐ΤᏧ௦Іᴑ܁𝐬𝐰𝐲𝐛𝐦𝐯𝐑𝐙𝐣𝐇𝐂𝐘𝟎ԜТᗞ౦〔Ꭻ𝐳𝐔𝐱𝟔𝟓𝐅🐋ﬃ💘💓ё𝘥𝘯𝘶💐🌋🌄🌅𝙬𝙖𝙨𝙤𝙣𝙡𝙮𝙘𝙠𝙚𝙙𝙜𝙧𝙥𝙩𝙪𝙗𝙞𝙝𝙛👺🐷ℋ𝐀𝐥𝐪🚶𝙢Ἱ🤘ͦ💸ج패티Ｗ𝙇ᵻ👂👃ɜ🎫\uf0a7БУі🚢🚂ગુજરાતીῆ🏃𝓬𝓻𝓴𝓮𝓽𝓼☘﴾̯﴿₽\ue807𝑻𝒆𝒍𝒕𝒉𝒓𝒖𝒂𝒏𝒅𝒔𝒎𝒗𝒊👽😙\u200cЛ‒🎾👹⎌🏒⛸公寓养宠物吗🏄🐀🚑🤷操美𝒑𝒚𝒐𝑴🤙🐒欢迎来到阿拉斯ספ𝙫🐈𝒌𝙊𝙭𝙆𝙋𝙍𝘼𝙅ﷻ🦄巨收赢得白鬼愤怒要买额ẽ🚗🐳𝟏𝐟𝟖𝟑𝟕𝒄𝟗𝐠𝙄𝙃👇锟斤拷𝗢𝟳𝟱𝟬⦁マルハニチロ株式社⛷한국어ㄸㅓ니͜ʖ𝘿𝙔₵𝒩ℯ𝒾𝓁𝒶𝓉𝓇𝓊𝓃𝓈𝓅ℴ𝒻𝒽𝓀𝓌𝒸𝓎𝙏ζ𝙟𝘃𝗺𝟮𝟭𝟯𝟲👋🦊多伦🐽🎻🎹⛓🏹🍷🦆为和中友谊祝贺与其想象对法如直接问用自己猜本传教士没积唯认识基督徒曾经让相信耶稣复活死怪他但当们聊些政治题时候战胜因圣把全堂结婚孩恐惧且栗谓这样还♾🎸🤕🤒⛑🎁批判检讨🏝🦁🙋😶쥐스탱트뤼도석유가격인상이경제황을렵게만들지않록잘관리해야합다캐나에서대마초와화약금의품런성분갈때는반드시허된사용🔫👁凸ὰ💲🗯𝙈Ἄ𝒇𝒈𝒘𝒃𝑬𝑶𝕾𝖙𝖗𝖆𝖎𝖌𝖍𝖕𝖊𝖔𝖑𝖉𝖓𝖐𝖜𝖞𝖚𝖇𝕿𝖘𝖄𝖛𝖒𝖋𝖂𝕴𝖟𝖈𝕸👑🚿💡知彼百\uf005𝙀𝒛𝑲𝑳𝑾𝒋𝟒😦𝙒𝘾𝘽🏐𝘩𝘨ὼṑ𝑱𝑹𝑫𝑵𝑪🇰🇵👾ᓇᒧᔭᐃᐧᐦᑳᐨᓃᓂᑲᐸᑭᑎᓀᐣ🐄🎈🔨🐎🤞🐸💟🎰🌝🛳点击查版🍭𝑥𝑦𝑧ＮＧ👣\uf020っ🏉ф💭🎥Ξ🐴👨🤳🦍\x0b🍩𝑯𝒒😗𝟐🏂👳🍗🕉🐲چی𝑮𝗕𝗴🍒ꜥⲣⲏ🐑⏰鉄リ事件ї💊「」\uf203\uf09a\uf222\ue608\uf202\uf099\uf469\ue607\uf410\ue600燻製シ虚偽屁理屈Г𝑩𝑰𝒀𝑺🌤𝗳𝗜𝗙𝗦𝗧🍊ὺἈἡχῖΛ⤏🇳𝒙ψՁմեռայինրւդձ冬至ὀ𝒁🔹🤚🍎𝑷🐂💅𝘬𝘱𝘸𝘷𝘐𝘭𝘓𝘖𝘹𝘲𝘫کΒώ💢ΜΟΝΑΕ🇱♲𝝈↴💒⊘Ȼ🚴🖕🖤🥘📍👈➕🚫🎨🌑🐻𝐎𝐍𝐊𝑭🤖🎎😼🕷ｇｒｎｔｉｄｕｆｂｋ𝟰🇴🇭🇻🇲𝗞𝗭𝗘𝗤👼📉🍟🍦🌈🔭《🐊🐍\uf10aლڡ🐦\U0001f92f\U0001f92a🐡💳ἱ🙇𝗸𝗟𝗠𝗷🥜さようなら🔼'

In [4]:
goodwords_replacer = [
    ("sh*t", "shit"),
    ("s**t", "shit"),
    ("f*ck", "fuck"),
    ("fu*k", "fuck"),
    ("f**k", "fuck"),
    ("f*****g", "fucking"),
    ("f***ing", "fucking"),
    ("f**king", "fucking"),
    ("p*ssy", "pussy"),
    ("p***y", "pussy"),
    ("pu**y", "pussy"),
    ("p*ss", "piss"),
    ("b*tch", "bitch"),
    ("bit*h", "bitch"),
    ("h*ll", "hell"),
    ("h**l", "hell"),
    ("cr*p", "crap"),
    ("d*mn", "damn"),
    ("stu*pid", "stupid"),
    ("st*pid", "stupid"),
    ("n*gger", "nigger"),
    ("n***ga", "nigger"),
    ("f*ggot", "faggot"),
    ("scr*w", "screw"),
    ("pr*ck", "prick"),
    ("g*d", "god"),
    ("s*x", "sex"),
    ("a*s", "ass"),
    ("a**hole", "asshole"),
    ("a***ole", "asshole"),
    ("a**", "ass"),
]

In [ ]:
## cleaning smile emoji
text = re.sub("\(:", " smile ", text)
## cleaning the penis asci art...
text = re.sub('8=+D', 'dick', text)

In [5]:
#HappyEmoticons
emoticons_happy = set([
    ':-)', ':)', ';)', ':o)', ':]', ':3', ':c)', ':>', '=]', '8)', '=)', ':}',
    ':^)', ':-D', ':D', '8-D', '8D', 'x-D', 'xD', 'X-D', 'XD', '=-D', '=D',
    '=-3', '=3', ':-))', ":'-)", ":')", ':*', ':^*', '>:P', ':-P', ':P', 'X-P',
    'x-p', 'xp', 'XP', ':-p', ':p', '=p', ':-b', ':b', '>:)', '>;)', '>:-)',
    '<3'
    ])

In [6]:
# Sad Emoticons
emoticons_sad = set([
    ':L', ':-/', '>:/', ':S', '>:[', ':@', ':-(', ':[', ':-||', '=L', ':<',
    ':-[', ':-<', '=\\', '=/', '>:(', ':(', '>.<', ":'-(", ":'(", ':\\', ':-c',
    ':c', ':{', '>:\\', ';('
    ])

In [7]:
#Emoji patterns
emoji_pattern = re.compile("["
         u"\U0001F600-\U0001F64F"  # emoticons
         u"\U0001F300-\U0001F5FF"  # symbols & pictographs
         u"\U0001F680-\U0001F6FF"  # transport & map symbols
         u"\U0001F1E0-\U0001F1FF"  # flags (iOS)
         u"\U00002702-\U000027B0"
         u"\U000024C2-\U0001F251"
         "]+", flags=re.UNICODE)

In [8]:
'U0001F600'

'U0001F600'

In [11]:
TweetTokenizer().tokenize("hello 😀")

['hello', '😀']

In [2]:
print(emoji.emojize(":grinning_face_with_big_eyes:")) 
print(emoji.emojize(":winking_face_with_tongue:")) 
print(emoji.emojize(":zipper-mouth_face:")) 

😃
😜
🤐


In [38]:
'😀'.translate('ger')

'😀'

In [45]:
'hello'.translate('привет')

'hello'

In [3]:
print("\N{grinning face}") 

😀


In [4]:
print(emoji.emojize('Python is :thumbsup:', use_aliases=True))

Python is 👍


In [5]:
print(emoji.emojize('Python is :grinning_face:'))

Python is 😀


In [6]:
emoji.demojize('😀')

':grinning_face:'

In [7]:
emoji.UNICODE_EMOJI_ALIAS

{'🥇': ':1st_place_medal:',
 '🥈': ':2nd_place_medal:',
 '🥉': ':3rd_place_medal:',
 '🆎': ':ab:',
 '🏧': ':atm:',
 '🅰': ':a:',
 '🇦🇫': ':flag_for_Afghanistan:',
 '🇦🇱': ':flag_for_Albania:',
 '🇩🇿': ':flag_for_Algeria:',
 '🇦🇸': ':flag_for_American_Samoa:',
 '🇦🇩': ':flag_for_Andorra:',
 '🇦🇴': ':flag_for_Angola:',
 '🇦🇮': ':flag_for_Anguilla:',
 '🇦🇶': ':flag_for_Antarctica:',
 '🇦🇬': ':flag_for_Antigua_&_Barbuda:',
 '♒': ':aquarius:',
 '🇦🇷': ':flag_for_Argentina:',
 '♈': ':aries:',
 '🇦🇲': ':flag_for_Armenia:',
 '🇦🇼': ':flag_for_Aruba:',
 '🇦🇨': ':flag_for_Ascension_Island:',
 '🇦🇺': ':flag_for_Australia:',
 '🇦🇹': ':flag_for_Austria:',
 '🇦🇿': ':flag_for_Azerbaijan:',
 '🔙': ':back:',
 '🅱': ':b:',
 '🇧🇸': ':flag_for_Bahamas:',
 '🇧🇭': ':flag_for_Bahrain:',
 '🇧🇩': ':flag_for_Bangladesh:',
 '🇧🇧': ':flag_for_Barbados:',
 '🇧🇾': ':flag_for_Belarus:',
 '🇧🇪': ':flag_for_Belgium:',
 '🇧🇿': ':flag_for_Belize:',
 '🇧🇯': ':flag_for_Benin:',
 '🇧🇲': ':flag_for_Bermuda:',
 '🇧🇹': ':flag_for_Bhutan:',
 '🇧🇴': ':flag_for_B

In [8]:
emoji.emoji_lis('helsdsdlo 😀sdsds')

[{'emoji': '😀', 'location': 10}]

In [9]:
emoji.emoji_lis('helsdsdlo 😀sdsds')[0]['location']

10

In [10]:
emoji.UNICODE_EMOJI

{'🥇': ':1st_place_medal:',
 '🥈': ':2nd_place_medal:',
 '🥉': ':3rd_place_medal:',
 '🆎': ':AB_button_(blood_type):',
 '🏧': ':ATM_sign:',
 '🅰': ':A_button_(blood_type):',
 '🇦🇫': ':Afghanistan:',
 '🇦🇱': ':Albania:',
 '🇩🇿': ':Algeria:',
 '🇦🇸': ':American_Samoa:',
 '🇦🇩': ':Andorra:',
 '🇦🇴': ':Angola:',
 '🇦🇮': ':Anguilla:',
 '🇦🇶': ':Antarctica:',
 '🇦🇬': ':Antigua_&_Barbuda:',
 '♒': ':Aquarius:',
 '🇦🇷': ':Argentina:',
 '♈': ':Aries:',
 '🇦🇲': ':Armenia:',
 '🇦🇼': ':Aruba:',
 '🇦🇨': ':Ascension_Island:',
 '🇦🇺': ':Australia:',
 '🇦🇹': ':Austria:',
 '🇦🇿': ':Azerbaijan:',
 '🔙': ':BACK_arrow:',
 '🅱': ':B_button_(blood_type):',
 '🇧🇸': ':Bahamas:',
 '🇧🇭': ':Bahrain:',
 '🇧🇩': ':Bangladesh:',
 '🇧🇧': ':Barbados:',
 '🇧🇾': ':Belarus:',
 '🇧🇪': ':Belgium:',
 '🇧🇿': ':Belize:',
 '🇧🇯': ':Benin:',
 '🇧🇲': ':Bermuda:',
 '🇧🇹': ':Bhutan:',
 '🇧🇴': ':Bolivia:',
 '🇧🇦': ':Bosnia_&_Herzegovina:',
 '🇧🇼': ':Botswana:',
 '🇧🇻': ':Bouvet_Island:',
 '🇧🇷': ':Brazil:',
 '🇮🇴': ':British_Indian_Ocean_Territory:',
 '🇻🇬': ':British_Vir

In [15]:
emoji.demojize('😲')

':astonished_face:'

In [16]:
emoji.EMOJI_ALIAS_UNICODE

{':1st_place_medal:': '🥇',
 ':2nd_place_medal:': '🥈',
 ':3rd_place_medal:': '🥉',
 ':AB_button_(blood_type):': '🆎',
 ':ATM_sign:': '🏧',
 ':A_button_(blood_type):': '🅰',
 ':Afghanistan:': '🇦🇫',
 ':Albania:': '🇦🇱',
 ':Algeria:': '🇩🇿',
 ':American_Samoa:': '🇦🇸',
 ':Andorra:': '🇦🇩',
 ':Angola:': '🇦🇴',
 ':Anguilla:': '🇦🇮',
 ':Antarctica:': '🇦🇶',
 ':Antigua_&_Barbuda:': '🇦🇬',
 ':Aquarius:': '♒',
 ':Argentina:': '🇦🇷',
 ':Aries:': '♈',
 ':Armenia:': '🇦🇲',
 ':Aruba:': '🇦🇼',
 ':Ascension_Island:': '🇦🇨',
 ':Australia:': '🇦🇺',
 ':Austria:': '🇦🇹',
 ':Azerbaijan:': '🇦🇿',
 ':BACK_arrow:': '🔙',
 ':B_button_(blood_type):': '🅱',
 ':Bahamas:': '🇧🇸',
 ':Bahrain:': '🇧🇭',
 ':Bangladesh:': '🇧🇩',
 ':Barbados:': '🇧🇧',
 ':Belarus:': '🇧🇾',
 ':Belgium:': '🇧🇪',
 ':Belize:': '🇧🇿',
 ':Benin:': '🇧🇯',
 ':Bermuda:': '🇧🇲',
 ':Bhutan:': '🇧🇹',
 ':Bolivia:': '🇧🇴',
 ':Bosnia_&_Herzegovina:': '🇧🇦',
 ':Botswana:': '🇧🇼',
 ':Bouvet_Island:': '🇧🇻',
 ':Brazil:': '🇧🇷',
 ':British_Indian_Ocean_Territory:': '🇮🇴',
 ':British_Virgin_Is

In [19]:
emoji.emoji_count('😲')

1

In [22]:
emoji.get_emoji_regexp()

re.compile(r'(\👨\\u200d\❤\️\\u200d\💋\\u200d\👨|\👩\\u200d\❤\️\\u200d\💋\\u200d\👨|\👩\\u200d\❤\️\\u200d\💋\\u200d\👩|\🏴\\U000e0067\\U000e0062\\U000e0065\\U000e006e\\U000e0067\\U000e007f|\🏴\\U000e0067\\U000e0062\\U000e0073\\U000e0063\\U000e0074\\U000e007f|\🏴\\U000e0067\\U000e0062\\U000e0077\\U000e006c\\U000e0073\\U000e007f|\👨\\u200d\👨\\u200d\👦\\u200d\👦|\👨\\u200d\👨\\u200d\👧\\u200d\👦|\👨\\u200d\👨\\u200d\👧\\u200d\👧|\👨\\u200d\👩\\u200d\👦\\u200d\👦|\👨\\u200d\👩\\u200d\👧\\u200d\👦|\👨\\u200d\👩\\u200d\👧\\u200d\👧|\👩\\u200d\👩\\u200d\👦\\u200d\👦|\👩\\u200d\👩\\u200d\👧\\u200d\👦|\👩\\u200d\👩\\u200d\👧\\u200d\👧|\👨\\u200d\❤\️\\u200d\👨|\👩\\u200d\❤\️\\u200d\👨|\👩\\u200d\❤\️\\u200d\👩|\👱\🏿\\u200d\♂\️|\👱\🏻\\u200d\♂\️|\👱\🏾\\u200d\♂\️|\👱\🏼\\u200d\♂\️|\👱\🏽\\u200d\♂\️|\👱\🏿\\u200d\♀\️|\👱\🏻\\u200d\♀\️|\👱\🏾\\u200d\♀\️|\👱\🏼\\u200d\♀\️|\👱\🏽\\u200d\♀\️|\👁\️\\u200d\🗨\️|\👨\\u200d\👦\\u200d\👦|\👨\\u200d\👧\\u200d\👦|\👨\\u200d\👧\\u200d\👧|\👨\\u200d\👨\\u200d\👦|\👨\\u200d\👨\\u200d\👧|\👨\\u200d\👩\\u200d\👦|\👨\\u200d\👩\\u200d\👧|\👩\\u200d\👦\\u200d\👦|

In [24]:
print('u200d')

u200d


In [28]:
emoji.

TypeError: 'module' object is not callable

In [32]:
"\N{GREEK CAPITAL LETTER DELTA}"

'Δ'

In [11]:
emoji.emoji_lis('Δ')

[]

In [487]:
u = 'Δ'
f = '<'
print(ord(f))

60


In [36]:
'Δ'

'Δ'

In [37]:
'Δ'

'Δ'

In [497]:
U'\U0010ffff'

'\U0010ffff'

In [496]:
chr(1114111)

'\U0010ffff'

In [491]:
sys.maxunicode

1114111

In [479]:
print(ord(879))

TypeError: ord() expected string of length 1, but int found

In [72]:
"\N{Δ}"

SyntaxError: (unicode error) 'unicodeescape' codec can't decode bytes in position 0-13: unknown Unicode character name (<ipython-input-72-cf8838346cca>, line 1)

In [31]:
"\N{:grinning face with big eyes:}"

SyntaxError: (unicode error) 'unicodeescape' codec can't decode bytes in position 0-32: unknown Unicode character name (<ipython-input-31-d7fb0c7dc84e>, line 1)

In [29]:
s = '😀'
print(emoji.emojize(s)) 

😀


In [15]:
print(s.encode('unicode-escape').decode('ASCII'))

\U0001f600


In [16]:
a = s.encode('unicode-escape').decode('ASCII')

In [24]:
a.decode('utf-8')

AttributeError: 'str' object has no attribute 'decode'

In [23]:
"😀-🙏🌀-🗿🚀".encode('unicode-escape').decode('ASCII')

'\\U0001f600-\\U0001f64f\\U0001f300-\\U0001f5ff\\U0001f680'

In [25]:
re.compile("["u"hello"
         u"\U0001F600-\U0001F64F"  # emoticons
         u"\U0001F300-\U0001F5FF"  # symbols & pictographs
         u"\U0001F680-\U0001F6FF"  # transport & map symbols
         u"\U0001F1E0-\U0001F1FF"  # flags (iOS)
         u"\U00002702-\U000027B0"
         u"\U000024C2-\U0001F251"
         "]+", flags=re.UNICODE)

re.compile(r'[hello😀-🙏🌀-🗿🚀-\U0001f6ff\U0001f1e0-🇿✂-➰Ⓜ-🉑]+', re.UNICODE)

In [26]:
re.compile("["u"hello"
         "😀"
         "]+", flags=re.UNI)

re.compile(r'[hello😀]+', re.UNICODE)

In [8]:
emoji_pattern

re.compile(r'[😀-🙏🌀-🗿🚀-\U0001f6ff\U0001f1e0-🇿✂-➰Ⓜ-🉑]+', re.UNICODE)

In [8]:
appos = {
"aren't" : "are not",
"can't" : "cannot",
"couldn't" : "could not",
"didn't" : "did not",
"doesn't" : "does not",
"don't" : "do not",
"hadn't" : "had not",
"hasn't" : "has not",
"haven't" : "have not",
"he'd" : "he would",
"he'll" : "he will",
"he's" : "he is",
"i'd" : "I would",
"i'd" : "I had",
"i'll" : "I will",
"i'm" : "I am",
"isn't" : "is not",
"it's" : "it is",
"it'll":"it will",
"i've" : "I have",
"let's" : "let us",
"mightn't" : "might not",
"mustn't" : "must not",
"shan't" : "shall not",
"she'd" : "she would",
"she'll" : "she will",
"she's" : "she is",
"shouldn't" : "should not",
"that's" : "that is",
"there's" : "there is",
"they'd" : "they would",
"they'll" : "they will",
"they're" : "they are",
"they've" : "they have",
"we'd" : "we would",
"we're" : "we are",
"weren't" : "were not",
"we've" : "we have",
"what'll" : "what will",
"what're" : "what are",
"what's" : "what is",
"what've" : "what have",
"where's" : "where is",
"who'd" : "who would",
"who'll" : "who will",
"who're" : "who are",
"who's" : "who is",
"who've" : "who have",
"won't" : "will not",
"wouldn't" : "would not",
"you'd" : "you would",
"you'll" : "you will",
"you're" : "you are",
"you've" : "you have",
"'re": " are",
"wasn't": "was not",
"we'll":" will",
"didn't": "did not"
}

In [6]:
print(😀)

SyntaxError: invalid character in identifier (<ipython-input-6-bbbdef0d259b>, line 1)

In [123]:
%%time
phrase= alltext

patterns= [r'\W+']

    
for p in patterns:
    match= re.findall(p, phrase)
#     print(match)

Wall time: 5.12 s


In [12]:
match

['\n',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 '? ',
 ' ',
 "'",
 ' ',
 ', ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 '. ',
 ' ',
 ' ',
 "'",
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 "'",
 ' ',
 ' ',
 '.',
 '.',
 '.',
 '.',
 ' ',
 "'",
 '! ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 "'",
 ' ',
 ' ',
 ' ',
 '. ',
 '.  (',
 ') ',
 ':',
 ', ',
 ' ',
 ', ',
 ' (',
 ') ',
 ' ',
 ', ',
 "'",
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 '. ',
 "'",
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 '. ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 '. "\n',
 '\n',
 ' ',
 "'",
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' - ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ', ',
 ' ',
 ' ',
 ' ',
 ' ""',
 ' ',
 ' ',
 '""  -',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 ' ',
 '.

In [124]:
mytext = ''
for i in match:
    mytext = " ".join(i)

In [407]:
mytext = ''

In [408]:
mytext

''

In [409]:
mytext = " ".join(i for i in match)

In [410]:
len(mytext)

24827900

In [411]:
def cleaning_data(noizy_comment):
#     noizy_comment= re.sub(r'http\S+', '', noizy_comment)
    noizy_comment = noizy_comment.lower()
    noizy_comment = re.sub(r'\n',' ',noizy_comment)
    noizy_comment = re.sub(' +',' ',noizy_comment)
    noizy_comment = noizy_comment.strip(' ')
    cleaned_comment = noizy_comment
    return cleaned_comment


In [412]:
mytext = cleaning_data(mytext)

In [413]:
len(mytext)

4662555

In [414]:
mytext[0:100]

'? \' , . \' \' . . . . \' ! \' . . ( ) : , , ( ) , \' . \' . . " \' - , "" "" - . , - - . . \' : # " , , . \' '

In [415]:
mytext = mytext.replace(u'\xa0', '')
# mytext = mytext.replace(" +", " ")
# mytext = mytext.replace("\n", " ")


In [416]:
len(mytext)

4656164

In [277]:
mytext

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.


In [417]:
'dfdfd....'.translate(str.maketrans('', '', string.punctuation))

'dfdfd'

In [418]:
mytext = mytext.translate(str.maketrans('', '', string.punctuation))

In [419]:
len(mytext)

2140399

In [420]:
mytext

'                                                     ·                                                    • •                                                   • •                                                                                                                                                                                                                                                                                                                                      —                                                                                                                                                                                                                    “  ‘    ’  ”                            “ ”                                                                                                                                                                                                                                                       –      

In [421]:
mytext

'                                                     ·                                                    • •                                                   • •                                                                                                                                                                                                                                                                                                                                      —                                                                                                                                                                                                                    “  ‘    ’  ”                            “ ”                                                                                                                                                                                                                                                       –      

In [422]:
mytext = " ".join(mytext.split())

In [423]:
len(mytext)

68022

In [424]:
mytext

'· • • • • — “ ‘ ’ ” “ ” – – 「」¤•¢ — — — — ം ാ ം ോ ് ോ െ ് ോ • · · — · ¡ ¿ † ‡ ↔ ↑ ↓ • ¶ ∞ ‘ “ ’ ” «» ¤ ₳ ฿ ₵ ¢ ₡ ₢ ₫ ₯ € ₠ ₣ ₴ ₭ ₤ ₥ ₦ № ₧ ₰ £ ៛ ₨ ₪ ৳ ₮ ₩ ¥ ♠ ♣ ♥ ♦ ̪ ̪ ̪ − —— →™ ☎☓ – – ✰✰ ♥♥ ♥♥ ´ ´ ´ ´ — — — — — ♫ § → → → →₪ – – – “ ” ⋅ ´ – — ☼ £ — ⋅ ⋅ — — — ♠♥♦♣ – 🗽 — • ₪— · └ ┐ – — — — ¨ ¨ ¨ ¨ ¨ ¨ — – ☎ — “ ” “ ” — — • – ּ ִ ְ ַ ִ ָ ַ ֶ ּ ִ ְ ֶ ֲ ָ ִ ְ ֶ ְ ָ ִ ְ ֶ ַ ְ ֻּ ִ ♦ —— — — ♫ — • ≈ ≈ “ ” “ ” – ⋅ ♥♥♥♥♥♥♥♥♥ — • • · — — → – ’ ‘ ’ ’ — — ♠♣♥♦™№ ©♪♫® – ► — → → – · · · ☼ ·· ·· ♥ — ’ ’ ’ ’ ’ ’ — — — ’ ’ ’ — — – £ • — —• ¨ — • ® ’ ” – ‘ ’ ´ ´ ’ ‘ ’ ‘ ’ ’ ‘ ’ ‘ ’ ‘ ’ ’ ‘ ’ ‘ ’ ’ ‘ ’ ´ ´ ‘ ’ ‘ ’ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ • • • • • • • • • • • • • • • • • • • • — § – — ⇔ ¦ ⇒✉ ☿ – “ ” – – — • — ¢ ☥ – — ’ ’ ’ — \u200e — — • ’ ’ ’ – ’ ’ ’ … ’ ’ → → → – ° — — ——————————————————————————————————————————————————————————— — — — ☏ – “ ” – — — • — ¢ \u200e ✰✰ “ ” “ ” \u200e • — • • — • – –– — • — — « » ˜ — ☺ — • • — • • \u200e – – \u200b\u200b \u200b\u200b \

In [425]:
for i in range(0,10):
    print(mytext[i])

·
 
•
 
•
 
•
 
•
 


In [426]:
len(mytext)

68022

In [427]:
e = emoji.emoji_lis(mytext)

In [428]:
len(e)

1866

In [429]:
e

[{'emoji': '↔', 'location': 78},
 {'emoji': '♠', 'location': 157},
 {'emoji': '♣', 'location': 159},
 {'emoji': '♥', 'location': 161},
 {'emoji': '♦', 'location': 163},
 {'emoji': '™', 'location': 177},
 {'emoji': '☎', 'location': 179},
 {'emoji': '♥', 'location': 189},
 {'emoji': '♥', 'location': 190},
 {'emoji': '♥', 'location': 192},
 {'emoji': '♥', 'location': 193},
 {'emoji': '♠', 'location': 260},
 {'emoji': '♥', 'location': 261},
 {'emoji': '♦', 'location': 262},
 {'emoji': '♣', 'location': 263},
 {'emoji': '🗽', 'location': 267},
 {'emoji': '☎', 'location': 306},
 {'emoji': '♦', 'location': 379},
 {'emoji': '♥', 'location': 410},
 {'emoji': '♥', 'location': 411},
 {'emoji': '♥', 'location': 412},
 {'emoji': '♥', 'location': 413},
 {'emoji': '♥', 'location': 414},
 {'emoji': '♥', 'location': 415},
 {'emoji': '♥', 'location': 416},
 {'emoji': '♥', 'location': 417},
 {'emoji': '♥', 'location': 418},
 {'emoji': '♠', 'location': 448},
 {'emoji': '♣', 'location': 449},
 {'emoji': '♥',

In [430]:
e_list = []
for i in e:
    print(i['emoji'])
    e_list.append(i['emoji'])

↔
♠
♣
♥
♦
™
☎
♥
♥
♥
♥
♠
♥
♦
♣
🗽
☎
♦
♥
♥
♥
♥
♥
♥
♥
♥
♥
♠
♣
♥
♦
™
©
®
♥
®
✉
☺
❤
☮
☺
☯
❤
☮
☺
☯
😜
♦
☯
♦
🍁
♦
☎
✍
♦
♦
®
®
♠
♠
™
😅
✉
©
🍌
🍌
✉
☺
✉
♦
♂
✉
♦
©
©
☎
♥
☎
♥
♥
♥
♥
©
™
☎
♣
♣
🗽
♠
♣
♥
♦
™
©
®
♥
♦
☯
🍁
✉
✉
✍
♦
♦
☺
♣
♣
☎
®
©
♀
♀
✉
♨
♨
♣
♣
♑
☀
✉
☄
☎
✉
☺
☺
♦
♥
♥
♥
♥
©
✉
♦
☎
✉
♠
♣
♥
♦
™
©
®
♠
♣
♥
♦
™
©
®
✔
✉
☎
♣
♣
☯
☺
☎
☎
♣
😊
✉
♠
♠
™
☎
☺
©
™
©
™
©
™
☺
♦
☺
♠
♣
♥
♦
™
☺
™
☎
☎
♥
♥
♥
☎
♦
®
©
☣
™
♦
♦
✔
♠
♥
♦
♣
❤
❤
☮
☺
☯
☎
♦
✉
✉
✉
✉
☮
😜
♦
♦
☎
☎
♠
♦
😂
😂
😂
♥
©
☎
♦
®
♣
♣
✍
✉
™
✉
♥
☎
♦
♥
©
♣
♣
😜
☮
☺
☎
☯
♣
♣
©
©
♥
😜
♠
♠
♠
♠
✈
😄
✉
☎
™
™
™
✍
♦
✔
☎
®
®
®
✔
✉
♥
♥
♠
♠
♠
♠
♥
♠
♣
♥
♦
™
✔
💬
♦
☠
✉
☺
©
™
♠
❤
☮
☺
☯
♠
♥
♦
♣
™
✉
✍
❤
®
☎
♦
☎
♥
♦
©
♣
♣
☺
♥
♦
❤
☮
☺
☯
☎
©
♥
♠
™
♠
©
❤
☮
☺
☯
☺
✈
☺
✍
♠
♣
♥
♦
™
©
®
❤
♥
☎
♦
♦
✍
☯
☯
♦
♦
♦
✔
©
😜
✔
✉
✔
☘
☘
™
✉
©
☎
♥
✉
☎
☮
☺
☎
✍
♥
🍁
♦
☎
☎
™
♣
♣
♥
♥
♥
♥
✔
✉
❤
☮
☺
☯
☎
♥
♠
♣
♥
♦
™
✉
✉
☸
☎
♥
♥
♥
♥
♥
©
☸
❤
☮
☺
☯
☎
☯
✉
♦
🍁
↗
☎
☎
☎
©
☎
♥
☎
✍
™
©
©
✍
☎
©
♥
♥
📞
📧
☮
♦
❤
☮
☺
☯
♥
♦
☎
®
😜
☎
✉
♠
♣
♥
♦
™
©
®
♦
♥
♥
©
☺
©
®
©
©
®
©
©
©
™
✔
♥
♥
♥
♥
♦
✉
☎
™
©
♣
☎
☎
☎
☄
©
✍
♦
©
☮
☺
©
♠
♠
©
♥
☎
♦
♣
♠


In [431]:
'♥' in e_list

True

In [432]:
for i in e_list:
    if i in mytext:
        mytext = mytext.replace(i, " ")

In [433]:
len(mytext)

68022

In [434]:
mytext[0:1000]

'· • • • • — “ ‘ ’ ” “ ” – – 「」¤•¢ — — — — ം ാ ം ോ ് ോ െ ് ോ • · · — · ¡ ¿ † ‡   ↑ ↓ • ¶ ∞ ‘ “ ’ ” «» ¤ ₳ ฿ ₵ ¢ ₡ ₢ ₫ ₯ € ₠ ₣ ₴ ₭ ₤ ₥ ₦ № ₧ ₰ £ ៛ ₨ ₪ ৳ ₮ ₩ ¥         ̪ ̪ ̪ − —— →   ☓ – – ✰✰       ´ ´ ´ ´ — — — — — ♫ § → → → →₪ – – – “ ” ⋅ ´ – — ☼ £ — ⋅ ⋅ — — —      –   — • ₪— · └ ┐ – — — — ¨ ¨ ¨ ¨ ¨ ¨ — –   — “ ” “ ” — — • – ּ ִ ְ ַ ִ ָ ַ ֶ ּ ִ ְ ֶ ֲ ָ ִ ְ ֶ ְ ָ ִ ְ ֶ ַ ְ ֻּ ִ   —— — — ♫ — • ≈ ≈ “ ” “ ” – ⋅           — • • · — — → – ’ ‘ ’ ’ — —      №  ♪♫  – ► — → → – · · · ☼ ·· ··   — ’ ’ ’ ’ ’ ’ — — — ’ ’ ’ — — – £ • — —• ¨ — •   ’ ” – ‘ ’ ´ ´ ’ ‘ ’ ‘ ’ ’ ‘ ’ ‘ ’ ‘ ’ ’ ‘ ’ ‘ ’ ’ ‘ ’ ´ ´ ‘ ’ ‘ ’ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ • • • • • • • • • • • • • • • • • • • • — § – — ⇔ ¦ ⇒  ☿ – “ ” – – — • — ¢ ☥ – — ’ ’ ’ — \u200e — — • ’ ’ ’ – ’ ’ ’ … ’ ’ → → → – ° — — ——————————————————————————————————————————————————————————— — — — ☏ – “ ” – — — • — ¢ \u200e ✰✰ “ ” “ ” \u200e • — • • — • – –– — • — — « » ˜ —   — • • — • • \u200e – – \u200b\u200b \u200b\u200b \

In [435]:
mytext = " ".join(mytext.split())

In [436]:
len(mytext)

64790

In [437]:
mytext

'· • • • • — “ ‘ ’ ” “ ” – – 「」¤•¢ — — — — ം ാ ം ോ ് ോ െ ് ോ • · · — · ¡ ¿ † ‡ ↑ ↓ • ¶ ∞ ‘ “ ’ ” «» ¤ ₳ ฿ ₵ ¢ ₡ ₢ ₫ ₯ € ₠ ₣ ₴ ₭ ₤ ₥ ₦ № ₧ ₰ £ ៛ ₨ ₪ ৳ ₮ ₩ ¥ ̪ ̪ ̪ − —— → ☓ – – ✰✰ ´ ´ ´ ´ — — — — — ♫ § → → → →₪ – – – “ ” ⋅ ´ – — ☼ £ — ⋅ ⋅ — — — – — • ₪— · └ ┐ – — — — ¨ ¨ ¨ ¨ ¨ ¨ — – — “ ” “ ” — — • – ּ ִ ְ ַ ִ ָ ַ ֶ ּ ִ ְ ֶ ֲ ָ ִ ְ ֶ ְ ָ ִ ְ ֶ ַ ְ ֻּ ִ —— — — ♫ — • ≈ ≈ “ ” “ ” – ⋅ — • • · — — → – ’ ‘ ’ ’ — — № ♪♫ – ► — → → – · · · ☼ ·· ·· — ’ ’ ’ ’ ’ ’ — — — ’ ’ ’ — — – £ • — —• ¨ — • ’ ” – ‘ ’ ´ ´ ’ ‘ ’ ‘ ’ ’ ‘ ’ ‘ ’ ‘ ’ ’ ‘ ’ ‘ ’ ’ ‘ ’ ´ ´ ‘ ’ ‘ ’ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ • • • • • • • • • • • • • • • • • • • • — § – — ⇔ ¦ ⇒ ☿ – “ ” – – — • — ¢ ☥ – — ’ ’ ’ — \u200e — — • ’ ’ ’ – ’ ’ ’ … ’ ’ → → → – ° — — ——————————————————————————————————————————————————————————— — — — ☏ – “ ” – — — • — ¢ \u200e ✰✰ “ ” “ ” \u200e • — • • — • – –– — • — — « » ˜ — — • • — • • \u200e – – \u200b\u200b \u200b\u200b \u200b\u200b \u200b\u200b — • ’ ₪— · « – ু া ુ ા ु ा ು

In [468]:
unicodedata.name('”')

'RIGHT DOUBLE QUOTATION MARK'

In [439]:
len(set(mytext))

416

In [466]:
for i in set(mytext):
    print(i)

‽
⊂
◕
ெ
̲

₫
○
，
˺
ं
➜
₰
ॆ
ָ
ّ
‖
̆

′
？
ુ
₡
ُ
̗
़
ा
◯
₠
！
¦
➔
ே
∀
∇
∅
¶
┏
ֶ
✤
☭
₳
✐
┃
◦
ृ
ٔ
⇄
่


ͤ
±
ৌ
̹

ਾ
╩
╗
∈
‬
ີ
┓
ͮ
⟲
★
⊗
➥
┌
❉
ি

ິ
⊥

―
）
ִ
《
׀
ົ
₨
͓
”
│
´

̓
⇒
₥
∙
͑
❝
ை
̉
ູ
₩
͡
₢
×
͙
‿
ַ
❦
☓
♚
̜
⁓
－
✗
₪
ி
∑
÷
☏
├
ⓣ
̰
✿
∧
“
◔
⁞

₭
●
ែ
҉
♪
െ
︵
≡
ि
̴
➨
₵
•
♬
╢
҅
┐
‒
☼
ু
¬
〉
⊙
≤
】
ো
←
◁
ா
̞
ׁ
⟩
☿
¥
ோ
֑
ै
ు

⁂
↨
┛

͚
∞
́
்
☞
״
̄
☇

්
↑
ⓐ
̎
♔
❞
█
ে
✆
ຼ
̺
°
･
⨹
͖
ீ

¿
˜
◄
‫
ા
╚
¡
§
━
਼
ी
ֵ
｡
➪
„
€
»
◅
̼
۩
☾
﻿
℠
∗
’
⟨
►

↓

ຸ
⁄
✄
۬
۾

⊝
☥
·
ु
‐
‪
″
̈
ً
̂
༆
═
』
ְ
⁠
௹
ੁ
៛
ͨ
ͩ
ो
¨
ా
‏
❖
᾽
ּ
✰
്
⊕
：
⇔
ং
‧
。
（
▎
√
☻
๛
‘
／
्
¢
ු
­
☽
¯

̥
₯
̿
、
─
・
☤
—
̪
〈
�

✓
–
̠
۞

♫

№
₴
₤
┗
†

℥
¤

✭
‍
ോ
ಾ
☜
⁾
،
≽
☛
¸

া

͉
【
ு
̫
‎
┘
̮
​
✽
✞
■
ು
∫
ँ
ͧ
「
₣
✎
╦
▲
࿓
ุ
়
└
≼
╝
∆
ം
✫
ொ
〈

ֻ
→
̃
♝
♩
…
╔
⌊
᧾
⚇
△
◥
₧
『
−
⁽
£
̯
．
«
্
߷
㊟
║
╟
☆
₮
╫
ू

່
̭
҈
∴
͇
े
∂
≠
ֲ
≈
ാ
‑
្
‡
▾
฿
۝
」
✘
㎥
ັ
›
》
৳
ॉ
⋅
₦

͍
∪
‹
≥
⇝
̩


In [469]:
CUSTOM_TABLE = str.maketrans(
    {
        "\xad": None,
        "\x7f": None,
        "\ufeff": None,
        "\u200b": None,
        "\u200e": None,
        "\u202a": None,
        "\u202c": None,
        "‘": "'",
        "’": "'",
        "`": "'",
        "“": '"',
        "”": '"',
        "«": '"',
        "»": '"',
        "ɢ": "G",
        "ɪ": "I",
        "ɴ": "N",
        "ʀ": "R",
        "ʏ": "Y",
        "ʙ": "B",
        "ʜ": "H",
        "ʟ": "L",
        "ғ": "F",
        "ᴀ": "A",
        "ᴄ": "C",
        "ᴅ": "D",
        "ᴇ": "E",
        "ᴊ": "J",
        "ᴋ": "K",
        "ᴍ": "M",
        "Μ": "M",
        "ᴏ": "O",
        "ᴘ": "P",
        "ᴛ": "T",
        "ᴜ": "U",
        "ᴡ": "W",
        "ᴠ": "V",
        "ĸ": "K",
        "в": "B",
        "м": "M",
        "н": "H",
        "т": "T",
        "ѕ": "S",
        "—": "-",
        "–": "-",
    }
)

In [476]:
len(mytext.translate(CUSTOM_TABLE))

32533

In [472]:
import sys

In [473]:
# REGEX_REPLACER = [
#     (re.compile(pat.replace("*", "\*"), flags=re.IGNORECASE), repl)
#     for pat, repl in WORDS_REPLACER
# ]

# RE_SPACE = re.compile(r"\s")
# RE_MULTI_SPACE = re.compile(r"\s+")

NMS_TABLE = dict.fromkeys(
    i for i in range(sys.maxunicode + 1) if unicodedata.category(chr(i)) == "Mn"
)

HEBREW_TABLE = {i: "א" for i in range(0x0590, 0x05FF)}
ARABIC_TABLE = {i: "ا" for i in range(0x0600, 0x06FF)}
CHINESE_TABLE = {i: "是" for i in range(0x4E00, 0x9FFF)}
KANJI_TABLE = {i: "ッ" for i in range(0x2E80, 0x2FD5)}
HIRAGANA_TABLE = {i: "ッ" for i in range(0x3041, 0x3096)}
KATAKANA_TABLE = {i: "ッ" for i in range(0x30A0, 0x30FF)}

TABLE = dict()
TABLE.update(CUSTOM_TABLE)
TABLE.update(NMS_TABLE)
# Non-english languages
TABLE.update(CHINESE_TABLE)
TABLE.update(HEBREW_TABLE)
TABLE.update(ARABIC_TABLE)
TABLE.update(HIRAGANA_TABLE)
TABLE.update(KATAKANA_TABLE)
TABLE.update(KANJI_TABLE)

In [474]:
NMS_TABLE

{768: None,
 769: None,
 770: None,
 771: None,
 772: None,
 773: None,
 774: None,
 775: None,
 776: None,
 777: None,
 778: None,
 779: None,
 780: None,
 781: None,
 782: None,
 783: None,
 784: None,
 785: None,
 786: None,
 787: None,
 788: None,
 789: None,
 790: None,
 791: None,
 792: None,
 793: None,
 794: None,
 795: None,
 796: None,
 797: None,
 798: None,
 799: None,
 800: None,
 801: None,
 802: None,
 803: None,
 804: None,
 805: None,
 806: None,
 807: None,
 808: None,
 809: None,
 810: None,
 811: None,
 812: None,
 813: None,
 814: None,
 815: None,
 816: None,
 817: None,
 818: None,
 819: None,
 820: None,
 821: None,
 822: None,
 823: None,
 824: None,
 825: None,
 826: None,
 827: None,
 828: None,
 829: None,
 830: None,
 831: None,
 832: None,
 833: None,
 834: None,
 835: None,
 836: None,
 837: None,
 838: None,
 839: None,
 840: None,
 841: None,
 842: None,
 843: None,
 844: None,
 845: None,
 846: None,
 847: None,
 848: None,
 849: None,
 850: None,
 851

In [477]:
len(mytext.translate(TABLE))

32153

In [485]:
sys.maxunicode

1114111

In [486]:
unicodedata.category

<function unicodedata.category>

In [458]:
len(mytext.replace(' ', ''))

33323

In [459]:
mytext = mytext.replace(' ', '')

In [464]:
for i in set(mytext):
    
    print('{} : {}'.format(i, unicodedata.name(i)))

‽ : INTERROBANG
⊂ : SUBSET OF
◕ : CIRCLE WITH ALL BUT UPPER LEFT QUADRANT BLACK
ெ : TAMIL VOWEL SIGN E
̲ : COMBINING LOW LINE


ValueError: no such name

In [441]:
# def deEmojify(inputString):
#     return inputString.encode('ascii', 'ignore').decode('ascii')

In [443]:
string.ascii_letters

'abcdefghijklmnopqrstuvwxyzABCDEFGHIJKLMNOPQRSTUVWXYZ'

In [447]:
string.whitespace

' \t\n\r\x0b\x0c'

In [451]:
'\u200e  '.translate({ord(c): '' for c in string.whitespace})

'\u200e'

In [452]:
replchars = re.compile(r'[\n\r]')
def replchars_to_hex(match):
    return r'\x{0:02x}'.format(ord(match.group()))

replchars.sub(replchars_to_hex, mytext)

'· • • • • — “ ‘ ’ ” “ ” – – 「」¤•¢ — — — — ം ാ ം ോ ് ോ െ ് ോ • · · — · ¡ ¿ † ‡ ↑ ↓ • ¶ ∞ ‘ “ ’ ” «» ¤ ₳ ฿ ₵ ¢ ₡ ₢ ₫ ₯ € ₠ ₣ ₴ ₭ ₤ ₥ ₦ № ₧ ₰ £ ៛ ₨ ₪ ৳ ₮ ₩ ¥ ̪ ̪ ̪ − —— → ☓ – – ✰✰ ´ ´ ´ ´ — — — — — ♫ § → → → →₪ – – – “ ” ⋅ ´ – — ☼ £ — ⋅ ⋅ — — — – — • ₪— · └ ┐ – — — — ¨ ¨ ¨ ¨ ¨ ¨ — – — “ ” “ ” — — • – ּ ִ ְ ַ ִ ָ ַ ֶ ּ ִ ְ ֶ ֲ ָ ִ ְ ֶ ְ ָ ִ ְ ֶ ַ ְ ֻּ ִ —— — — ♫ — • ≈ ≈ “ ” “ ” – ⋅ — • • · — — → – ’ ‘ ’ ’ — — № ♪♫ – ► — → → – · · · ☼ ·· ·· — ’ ’ ’ ’ ’ ’ — — — ’ ’ ’ — — – £ • — —• ¨ — • ’ ” – ‘ ’ ´ ´ ’ ‘ ’ ‘ ’ ’ ‘ ’ ‘ ’ ‘ ’ ’ ‘ ’ ‘ ’ ’ ‘ ’ ´ ´ ‘ ’ ‘ ’ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ • • • • • • • • • • • • • • • • • • • • — § – — ⇔ ¦ ⇒ ☿ – “ ” – – — • — ¢ ☥ – — ’ ’ ’ — \u200e — — • ’ ’ ’ – ’ ’ ’ … ’ ’ → → → – ° — — ——————————————————————————————————————————————————————————— — — — ☏ – “ ” – — — • — ¢ \u200e ✰✰ “ ” “ ” \u200e • — • • — • – –– — • — — « » ˜ — — • • — • • \u200e – – \u200b\u200b \u200b\u200b \u200b\u200b \u200b\u200b — • ’ ₪— · « – ু া ુ ા ु ा ು

In [456]:
'\u200cHealth & Fitness'.isprintable()

False

In [365]:
u'\u200cHealth & Fitness'.encode('ascii', 'ignore').decode('unicode_escape')

'Health & Fitness'

In [356]:
mytext[0:1000]

'· • • • • — “ ‘ ’ ” “ ” – – 「」¤•¢ — — — — ം ാ ം ോ ് ോ െ ് ോ • · · — · ¡ ¿ † ‡ ↑ ↓ • ¶ ∞ ‘ “ ’ ” «» ¤ ₳ ฿ ₵ ¢ ₡ ₢ ₫ ₯ € ₠ ₣ ₴ ₭ ₤ ₥ ₦ № ₧ ₰ £ ៛ ₨ ₪ ৳ ₮ ₩ ¥ ̪ ̪ ̪ − —— → ☓ – – ✰✰ ´ ´ ´ ´ — — — — — ♫ § → → → →₪ – – – “ ” ⋅ ´ – — ☼ £ — ⋅ ⋅ — — — – — • ₪— · └ ┐ – — — — ¨ ¨ ¨ ¨ ¨ ¨ — – — “ ” “ ” — — • – ּ ִ ְ ַ ִ ָ ַ ֶ ּ ִ ְ ֶ ֲ ָ ִ ְ ֶ ְ ָ ִ ְ ֶ ַ ְ ֻּ ִ —— — — ♫ — • ≈ ≈ “ ” “ ” – ⋅ — • • · — — → – ’ ‘ ’ ’ — — № ♪♫ – ► — → → – · · · ☼ ·· ·· — ’ ’ ’ ’ ’ ’ — — — ’ ’ ’ — — – £ • — —• ¨ — • ’ ” – ‘ ’ ´ ´ ’ ‘ ’ ‘ ’ ’ ‘ ’ ‘ ’ ‘ ’ ’ ‘ ’ ‘ ’ ’ ‘ ’ ´ ´ ‘ ’ ‘ ’ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ ‘ ’ • • • • • • • • • • • • • • • • • • • • — § – — ⇔ ¦ ⇒ ☿ – “ ” – – — • — ¢ ☥ – — ’ ’ ’ — \u200e — — • ’ ’ ’ – ’ ’ ’ … ’ ’ → → → – ° — — ——————————————————————————————————————————————————————————— — — — ☏ – “ ” – — — • — ¢ \u200e ✰✰ “ ” “ ” \u200e • — • • — • – –– — • — — « » ˜ — — • • — • • \u200e – – \u200b\u200b \u200b\u200b \u200b\u200b \u200b\u200b — • ’ ₪— · « – ু া ુ ા ु ा ು

In [397]:
mytext = mytext.encode('ascii', 'ignore').decode('unicode_escape')

In [398]:
len(mytext)

31468

In [399]:
mytext

'                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       

In [400]:
mytext[0:1000]

'                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       

In [ ]:
2140399

In [401]:
mytext = mytext.replace(" +", "")

In [402]:
len(mytext)

31468

In [403]:
mytext

'                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       

In [404]:
unicodedata.name('☎')

'BLACK TELEPHONE'

In [405]:
for i in mytext:
    mytext = mytext.replace(i, unicodedata.name(i)) 

ValueError: no such name

In [406]:
mytext[0:100]

'SPACESPACESPACESPACESPACESPACESPACESPACESPACESPACESPACESPACESPACESPACESPACESPACESPACESPACESPACESPACE'

In [294]:
'♦' in e[0]

False

In [ ]:
aa

In [228]:
'↔' in e

False

In [229]:
type(e)

list

In [236]:
'😀'.translate(str.maketrans(' ', ' ', i['emoji']))

'😀'

In [230]:
for i in e:
    if i['emoji'] in mytext:
        mytext = mytext.translate(str.maketrans('', '', i['emoji']))

In [231]:
len(mytext)

4660689

In [ ]:
2599140

In [200]:
for i in range(0,100):
    print(mytext[i])

 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
·
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 


In [82]:
unicodedata.name('ം')

'MALAYALAM SIGN ANUSVARA'

In [201]:
mytext

'                                                         ·                                                          • •                                                    • •                                                                                                                                                                                                                                                                                                                                                                                                                    —                                                                                                                                                                                                                                                              “  ‘    ’   ”                                               “ ”                                                                                                       

In [99]:
unicodedata.name('☎')

'BLACK TELEPHONE'

In [108]:
b"\xa0\xa0\xa0".encode("utf-8") 

AttributeError: 'bytes' object has no attribute 'encode'

In [115]:
b'\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0'.encode("utf-8") 

AttributeError: 'bytes' object has no attribute 'encode'

In [117]:
h'&#xa0'.decode("utf-8") 

SyntaxError: invalid syntax (<ipython-input-117-f70f0175c89a>, line 1)

In [122]:
hex(b'\xa0')

TypeError: 'bytes' object cannot be interpreted as an integer

In [92]:
re.compile("["
         u"\xa0"  # emoticons
#          u"\U0001F300-\U0001F5FF"  # symbols & pictographs
#          u"\U0001F680-\U0001F6FF"  # transport & map symbols
#          u"\U0001F1E0-\U0001F1FF"  # flags (iOS)
#          u"\U00002702-\U000027B0"
#          u"\U000024C2-\U0001F251"
         "]+", flags=re.UNICODE)

re.compile(r'[\xa0]+', re.UNICODE)

In [93]:
b'\x80abc'.decode("utf-8", "strict")  

UnicodeDecodeError: 'utf-8' codec can't decode byte 0x80 in position 0: invalid start byte

In [94]:
'PR\xc3\x86KVAL'.encode('ascii')

UnicodeEncodeError: 'ascii' codec can't encode characters in position 2-3: ordinal not in range(128)

In [ ]:
for idx, i in enumerate(mytext):
    

In [78]:
from datetime import datetime

In [79]:
datetime.strptime(dateRegistered.strip('\u200e'), '%m-%d-%Y%I:%M %p')

NameError: name 'dateRegistered' is not defined

In [ ]:
aaaaaaa